### Create the intermediate layer of the air travel lakehouse



#### Setup

##### Declare the global variables

In [ ]:
project_id = "cs378-fa2025"
region = "us-central1"
int_dataset = "air_travel_int"
model_dataset = "air_travel_model"

In [ ]:
from google.cloud import bigquery
bq_client = bigquery.Client()

##### Create two new BQ datasets, one for storing the intermediate tables and the other for the embeddings model

In [ ]:
dataset_id = bigquery.Dataset(f"{project_id}.{int_dataset}")
dataset_id.location = region
resp = bq_client.create_dataset(dataset_id, exists_ok=True)
print("Created dataset {}.{}".format(bq_client.project, resp.dataset_id))

Created dataset cs378-fa2025.air_travel_int


In [ ]:
dataset_id = bigquery.Dataset(f"{project_id}.{model_dataset}")
dataset_id.location = region
resp = bq_client.create_dataset(dataset_id, exists_ok=True)
print("Created dataset {}.{}".format(bq_client.project, resp.dataset_id))

Created dataset cs378-fa2025.air_travel_model


##### Create the connection resource to Vertex AI, this will allow us to call the AI models (gemini and embeddings) from BQ

In [ ]:
!bq mk --f=true --connection --location=$region --project_id=$project_id --connection_type=CLOUD_RESOURCE vertex-ai-connection

BigQuery error in mk operation: Already Exists: Connection
projects/988876466742/locations/us-central1/connections/vertex-ai-connection


In [ ]:
!bq show --connection 988876466742.us-central1.vertex-ai-connection

Connection 988876466742.us-central1.vertex-ai-connection

                      name                        friendlyName   description    Last modified         type        hasCredential                                            properties                                            
 ----------------------------------------------- -------------- ------------- ----------------- ---------------- --------------- ----------------------------------------------------------------------------------------------- 
  988876466742.us-central1.vertex-ai-connection                                10 Oct 19:01:26   CLOUD_RESOURCE   False           {"serviceAccountId": "bqcx-988876466742-37va@gcp-sa-bigquery-condel.iam.gserviceaccount.com"}  



In [ ]:
!gcloud projects add-iam-policy-binding $project_id \
  --member=serviceAccount:bqcx-988876466742-37va@gcp-sa-bigquery-condel.iam.gserviceaccount.com \
  --role=roles/aiplatform.user --format="none"

Updated IAM policy for project [cs378-fa2025].


##### Register the embeddings model with BigQuery

In [ ]:
%%bigquery
create or replace model `air_travel_model.embedding_model`
  remote with connection `us-central1.vertex-ai-connection`
  options(endpoint = 'text-embedding-005')

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

#### Create the Country table (resolving anomaly type 8)

In [ ]:
%%bigquery
select * from air_travel_stg.countries
order by name

Query is running:   0%|          |

Downloading:   0%|          |

name iso_code dafif_code _data_source  \
0                  Afghanistan       AF         AF  openflights   
1                      Albania       AL         AL  openflights   
2                      Algeria       DZ         AG  openflights   
3               American Samoa       AS         AQ  openflights   
4                       Angola       AO         AO  openflights   
..                         ...      ...        ...          ...   
256  Wallis and Futuna Islands       WF         WF  openflights   
257             Western Sahara       EH         WI  openflights   
258                      Yemen       YE         YM  openflights   
259                     Zambia       ZM         ZA  openflights   
260                   Zimbabwe       ZW         ZI  openflights   

                          _load_time  
0   2025-09-05 17:07:49.475555+00:00  
1   2025-09-05 17:07:49.475555+00:00  
2   2025-09-05 17:07:49.475555+00:00  
3   2025-09-05 17:07:49.475555+00:00  
4   2025-09-05 17:07:49.475555+00:00  
..                               ...  
256 2025-09-05 17:07:49.475555+00:00  
257 2025-09-05 17:07:49.475555+00:00  
258 2025-09-05 17:07:49.475555+00:00  
259 2025-09-05 17:07:49.475555+00:00  
260 2025-09-05 17:07:49.475555+00:00  

[261 rows x 5 columns]

In [ ]:
%%bigquery
select * from air_travel_stg.countries
where iso_code is null

Query is running:   0%|          |

Downloading:   0%|          |

name iso_code dafif_code _data_source  \
0                       Namibia     None         WA  openflights   
1              Glorioso Islands     None         GO  openflights   
2                 Palmyra Atoll     None         LQ  openflights   
3                 Jarvis Island     None         DQ  openflights   
4                   Wake Island     None         WQ  openflights   
5                     Jan Mayen     None         JN  openflights   
6                Midway Islands     None         MQ  openflights   
7               Paracel Islands     None         PF  openflights   
8   Ashmore and Cartier Islands     None         AT  openflights   
9               Tromelin Island     None         TE  openflights   
10               Howland Island     None         HQ  openflights   
11          Juan de Nova Island     None         JU  openflights   
12            Clipperton Island     None         IP  openflights   
13            Coral Sea Islands     None         CR  openflights   
14                 Baker Island     None         FQ  openflights   
15               Navassa Island     None         BQ  openflights   
16              Spratly Islands     None         PG  openflights   
17                Europa Island     None         EU  openflights   
18                 Kingman Reef     None         KQ  openflights   
19               Johnston Atoll     None         JQ  openflights   

                         _load_time  
0  2025-09-05 17:07:49.475555+00:00  
1  2025-09-05 17:07:49.475555+00:00  
2  2025-09-05 17:07:49.475555+00:00  
3  2025-09-05 17:07:49.475555+00:00  
4  2025-09-05 17:07:49.475555+00:00  
5  2025-09-05 17:07:49.475555+00:00  
6  2025-09-05 17:07:49.475555+00:00  
7  2025-09-05 17:07:49.475555+00:00  
8  2025-09-05 17:07:49.475555+00:00  
9  2025-09-05 17:07:49.475555+00:00  
10 2025-09-05 17:07:49.475555+00:00  
11 2025-09-05 17:07:49.475555+00:00  
12 2025-09-05 17:07:49.475555+00:00  
13 2025-09-05 17:07:49.475555+00:00  
14 2025-09-05 17:07:49.475555+00:00  
15 2025-09-05 17:07:49.475555+00:00  
16 2025-09-05 17:07:49.475555+00:00  
17 2025-09-05 17:07:49.475555+00:00  
18 2025-09-05 17:07:49.475555+00:00  
19 2025-09-05 17:07:49.475555+00:00

##### Look up the missing iso codes so we can use the iso_code field as the primary key for this table

In [ ]:
%%bigquery
create or replace table air_travel_tmp.countries_iso_codes as
  with countries_tmp as (
    select
      name,
      AI.GENERATE(
        ('What is the iso code for country ', name, '? If it does not have one, return None.'),
        connection_id => 'us-central1.vertex-ai-connection',
        endpoint => 'gemini-2.5-flash-lite',
        model_params => JSON '{"generation_config":{"thinking_config": {"thinking_budget": 0}}, "tools": [{"googleSearch": {}}]}',
        output_schema => 'iso_code STRING') as llm_response
    from air_travel_stg.countries
    where iso_code is null
  )
select name, llm_response.iso_code as mapped_iso_code
from countries_tmp

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
select * from air_travel_tmp.countries_iso_codes

Query is running:   0%|          |

Downloading:   0%|          |

name mapped_iso_code
0   Ashmore and Cartier Islands           AU-CQ
1                       Namibia              NA
2             Coral Sea Islands            None
3               Spratly Islands            None
4                 Europa Island            None
5                Navassa Island            None
6               Tromelin Island            None
7           Juan de Nova Island            None
8              Glorioso Islands            None
9               Paracel Islands             PAR
10            Clipperton Island              PN
11                    Jan Mayen              SJ
12               Midway Islands              UM
13                  Wake Island           UM-71
14                Jarvis Island           UM-74
15                Palmyra Atoll           UM-75
16                 Kingman Reef           UM-79
17               Johnston Atoll           UM-79
18               Howland Island           UM-79
19                 Baker Island           UM-80

##### Create the final table

In [ ]:
%%bigquery
create or replace table air_travel_int.Country as
    select iso_code, name, array_agg(ifnull(dafif_code, 'Unknown')) as dafif_codes, _data_source, _load_time
    from air_travel_stg.countries
    group by iso_code, name, _data_source, _load_time;

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
select * from air_travel_int.Country

Query is running:   0%|          |

Downloading:   0%|          |

iso_code              name dafif_codes _data_source  \
0       None   Paracel Islands        [PF]  openflights   
1       None           Namibia        [WA]  openflights   
2       None     Europa Island        [EU]  openflights   
3       None  Glorioso Islands        [GO]  openflights   
4       None         Jan Mayen        [JN]  openflights   
..       ...               ...         ...          ...   
254       YE             Yemen        [YM]  openflights   
255       YT           Mayotte        [MF]  openflights   
256       ZA      South Africa        [SF]  openflights   
257       ZM            Zambia        [ZA]  openflights   
258       ZW          Zimbabwe        [ZI]  openflights   

                          _load_time  
0   2025-09-05 17:07:49.475555+00:00  
1   2025-09-05 17:07:49.475555+00:00  
2   2025-09-05 17:07:49.475555+00:00  
3   2025-09-05 17:07:49.475555+00:00  
4   2025-09-05 17:07:49.475555+00:00  
..                               ...  
254 2025-09-05 17:07:49.475555+00:00  
255 2025-09-05 17:07:49.475555+00:00  
256 2025-09-05 17:07:49.475555+00:00  
257 2025-09-05 17:07:49.475555+00:00  
258 2025-09-05 17:07:49.475555+00:00  

[259 rows x 5 columns]

In [ ]:
%%bigquery
update air_travel_int.Country c
  set iso_code =
    (select mapped_iso_code from air_travel_tmp.countries_iso_codes i
     where c.name = i.name and i.mapped_iso_code is not null)
where iso_code is null

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
select * from air_travel_int.Country
where iso_code is null

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [iso_code, name, dafif_codes, _data_source, _load_time]
Index: []

In [ ]:
%%bigquery
select * from air_travel_int.Country
where array_length(dafif_codes) > 1
order by name

Query is running:   0%|          |

Downloading:   0%|          |

iso_code       name dafif_codes _data_source  \
0       IN      India    [BS, IN]  openflights   
1       PS  Palestine    [GZ, WE]  openflights   

                        _load_time  
0 2025-09-05 17:07:49.475555+00:00  
1 2025-09-05 17:07:49.475555+00:00

##### Check the primary key constraint

In [ ]:
%%bigquery
select name, count(*)
from air_travel_int.Country
group by name
having count(*) > 1

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [name, f0_]
Index: []

#### Create the `Airport` table (resolving anomaly type 9)

###### Goal: come up with a universal airport identifier. Intuitively, we would like to use the iata code for an airport because it is the one that most people are familiar with (e.g. AUS, JFK, ORD, etc.) The problem is that this code is not globally unique, and we would need to pair it up with the country where the airport is located.

###### Instead of `{iata, country}` as the unique identifier for an airport, we will opt to use the icao code, which is globally unique. Unfortunately, many records in the airport table are missing an icao code. We will use the LLM to look them up by iata and country, since this is public information that the language model knows about.

###### We want to end up with distinct airports in the airport table and only airports. We will therefore remove duplicate airport records and non-airports records.

###### Once the aiport table is ready, we will also have to re-create the child tables that depend on it. The child tables are: airport_maps, tsa_traffic, airport_reviews, flight_delays, and flight_routes. The new child tables will need to reference the records in the airport table via each airport's icao code.


In [ ]:
%%bigquery
select * from air_travel_stg.airports
where iata is not null
limit 10

Query is running:   0%|          |

Downloading:   0%|          |

id                        name        city        country iata  icao  \
0  13333              Istres Le Tube      Istres         France  QIE  None   
1  13163  Springer Municipal Airport    Springer  United States  S42  None   
2  12923                   Port Kent   Port Kent  United States  PRK  None   
3  13216            Diomede Heliport     Diomede  United States  DIO  None   
4  13534                Buli Airport        Buli      Indonesia  WUB  WAME   
5  12960                       OSRUI  Oconomowoc  United States  OCO  None   
6  13217  Marinda Raja Ampat Airport      Waisai      Indonesia  RJM  None   
7  13567             Gahcho Kue Mine  Gahcho Kue         Canada  GHK  None   
8  13149     Aztec Municipal Airport       Aztec  United States  N19  None   
9  13539     Jos Orno Imsula Airport      Tiakur      Indonesia  JIO  None   

    latitude   longitude  altitude  timezone_delta daylight_savings_time  \
0  43.312800    4.563000       161            <NA>                     U   
1  36.331522 -104.617851      5891              -6                     A   
2  44.525350  -73.402107        91              -5                     A   
3  65.758300 -168.953711        20              -9                     A   
4   0.881040  128.294030         5               9                     N   
5  43.109374  -88.485677       904              -6                     A   
6  -0.430246  130.774770       100               9                     U   
7  63.435300 -109.144700      1429              -6                     A   
8  36.836949 -108.028656      5882              -6                     A   
9  -8.140556  127.907222        13               9                     N   

  timezone_name  type source _data_source                       _load_time  
0          None  None   None  openflights 2025-09-05 17:06:39.719594+00:00  
1          None  None   None  openflights 2025-09-05 17:06:39.719594+00:00  
2          None  None   None  openflights 2025-09-05 17:06:39.719594+00:00  
3          None  None   None  openflights 2025-09-05 17:06:39.719594+00:00  
4          None  None   None  openflights 2025-09-05 17:06:39.719594+00:00  
5          None  None   None  openflights 2025-09-05 17:06:39.719594+00:00  
6          None  None   None  openflights 2025-09-05 17:06:39.719594+00:00  
7          None  None   None  openflights 2025-09-05 17:06:39.719594+00:00  
8          None  None   None  openflights 2025-09-05 17:06:39.719594+00:00  
9          None  None   None  openflights 2025-09-05 17:06:39.719594+00:00

##### Use the `AI.GENERATE` function to look up the icao code and the state or province that the airport is located in, since those details are missing from the table. Note that certain records already have icao codes which we can trust. We can use them as our ground truth and compare them to what we get back from the model.

In [ ]:
%%bigquery
with airport_tmp as (
  select
    name,
    country,
    iata,
    AI.GENERATE(
      ('What are the icao code and state/province for airport ', name, ' in country ', country, ' which has iata code of ', iata, '?'),
      connection_id => 'us-central1.vertex-ai-connection',
      endpoint => 'gemini-2.5-flash-lite',
      model_params => JSON '{"generation_config":{"thinking_config": {"thinking_budget": 0}}}',
      output_schema => 'icao STRING, state_province STRING') as llm_response
from air_travel_stg.airports
where iata is not null
limit 10
)
select name, country, iata, llm_response.icao as icao, llm_response.state_province as state_province
from airport_tmp

Query is running:   0%|          |

Downloading:   0%|          |

name        country iata  icao  \
0                       OSRUI  United States  OCO  KOSR   
1                Buli Airport      Indonesia  WUB  WUBB   
2                   Port Kent  United States  PRK  KPRK   
3     Jos Orno Imsula Airport      Indonesia  JIO  WIMG   
4  Springer Municipal Airport  United States  S42  KSPS   
5  Marinda Raja Ampat Airport      Indonesia  RJM  WJHR   
6     Aztec Municipal Airport  United States  N19  74AZ   
7              Istres Le Tube         France  QIE  LFMI   
8            Diomede Heliport  United States  DIO  PA38   
9             Gahcho Kue Mine         Canada  GHK  CEK4   

               state_province  
0                    Illinois  
1                  West Papua  
2               New Hampshire  
3            North Kalimantan  
4                    Oklahoma  
5                       Papua  
6                     Arizona  
7  Provence-Alpes-Côte d'Azur  
8                      Alaska  
9       Northwest Territories

In [ ]:
%%bigquery
select count(*) as icao_not_null
from air_travel_stg.airports
where icao is not null

Query is running:   0%|          |

Downloading:   0%|          |

icao_not_null
0           8160

In [ ]:
%%bigquery
select count(*) as icao_null
from air_travel_stg.airports
where icao is null

Query is running:   0%|          |

Downloading:   0%|          |

icao_null
0       4508

##### Evaluation

###### Run AI.GENERATE over a small sample (100 records) so we can compare the performance of the model before running over the full table. Warning: The full table takes about 22 minutes to run.

In [ ]:
%%bigquery
create or replace table air_travel_tmp.airport_llm_eval_flash_lite as
  with airport_tmp as (
    select
      name,
      country,
      iata,
      icao,
      AI.GENERATE(
        ('What is the icao code for airport ', name, ' in country ', country, ' which has iata code of ', iata, '?'),
        connection_id => 'us-central1.vertex-ai-connection',
        endpoint => 'gemini-2.5-flash-lite',
        model_params => JSON '{"generation_config":{"thinking_config": {"thinking_budget": 0}}, "tools": [{"googleSearch": {}}]}',
        output_schema => 'icao STRING') as llm_response
    from air_travel_stg.airports
    where iata is not null
    and icao is not null
    limit 100
  )
select name, country, iata, icao, llm_response.icao as llm_icao
from airport_tmp

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
create or replace table air_travel_tmp.airport_llm_eval_flash as
  with airport_tmp as (
    select
      name,
      country,
      iata,
      icao,
      AI.GENERATE(
        ('What is the icao code for airport ', name, ' in country ', country, ' which has iata code of ', iata, '?'),
        connection_id => 'us-central1.vertex-ai-connection',
        endpoint => 'gemini-2.5-flash',
        model_params => JSON '{"generation_config":{"thinking_config": {"thinking_budget": 0}}, "tools": [{"googleSearch": {}}]}',
        output_schema => 'icao STRING') as llm_response
    from air_travel_stg.airports
    where iata is not null
    and icao is not null
    limit 100
  )
select name, country, iata, icao, llm_response.icao as llm_icao
from airport_tmp

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
create or replace table air_travel_tmp.airport_llm_eval_pro as
  with airport_tmp as (
    select
      name,
      country,
      iata,
      icao,
      AI.GENERATE(
        ('What is the icao code for airport ', name, ' in country ', country, ' which has iata code of ', iata, '?'),
        connection_id => 'us-central1.vertex-ai-connection',
        endpoint => 'gemini-2.5-pro',
        model_params => JSON '{"generation_config":{"thinking_config": {"thinking_budget": 0}}, "tools": [{"googleSearch": {}}]}',
        output_schema => 'icao STRING') as llm_response
    from air_travel_stg.airports
    where iata is not null
    and icao is not null
    limit 100
  )
select name, country, iata, icao, llm_response.icao as llm_icao
from airport_tmp

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
select fl.icao as icao_fl, f.icao as icao_f, p.icao as icao_p
from air_travel_tmp.airport_llm_eval_flash_lite fl
join air_travel_tmp.airport_llm_eval_flash f on fl.name = f.name and fl.country = f.country
join air_travel_tmp.airport_llm_eval_pro p on f.name = p.name and f.country = p.country
where fl.icao != f.icao
or f.icao != p.icao

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [icao_fl, icao_f, icao_p]
Index: []

###### Since the icao results are the same across the three models, optimize for speed and cost and go with flash-lite. **Warning:** this query takes 22 minutes to run.

In [ ]:
%%bigquery
create or replace table air_travel_tmp.airport_llm as
  with airport_tmp as (
    select
      name,
      country,
      iata,
      AI.GENERATE(
        ('What are the icao code and state/province for airport ', name, ' in country ', country, ' which has an iata code of ', iata, '?'),
        connection_id => 'us-central1.vertex-ai-connection',
        endpoint => 'gemini-2.5-flash-lite',
        model_params => JSON '{"generation_config":{"thinking_config": {"thinking_budget": 0}}, "tools": [{"googleSearch": {}}]}',
        output_schema => 'icao STRING, state_prov STRING') as llm_response
    from air_travel_stg.airports
    where iata is not null
  )
select name, country, iata, llm_response.icao as llm_icao, llm_response.state_prov as llm_state_prov
from airport_tmp

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
select * from air_travel_tmp.airport_llm

Query is running:   0%|          |

Downloading:   0%|          |

name      country iata llm_icao  \
0                               Fayzabad Airport  Afghanistan  FBD     OAFZ   
1                         Mazar I Sharif Airport  Afghanistan  MZR     OAMS   
2                                Bamiyan Airport  Afghanistan  BIN     OABN   
3                                  Farah Airport  Afghanistan  FAH     OAFR   
4                                Maimana Airport  Afghanistan  MMZ     OAMN   
...                                          ...          ...  ...      ...   
6919  Joshua Mqabuko Nkomo International Airport     Zimbabwe  BUQ     FVBU   
6920                Hwange National Park Airport     Zimbabwe  HWN     FVHL   
6921        Victoria Falls International Airport     Zimbabwe  VFA     FVFA   
6922                          Thornhill Air Base     Zimbabwe  GWE     FVTR   
6923                                Bumi Airport     Zimbabwe  BZH     FVBU   

                   llm_state_prov  
0                      Badakhshan  
1                  Balkh Province  
2                Bamiyan Province  
3                  Farah Province  
4                 Faryab Province  
...                           ...  
6919           Matabeleland North  
6920           Matabeleland North  
6921  Matabeleland North Province  
6922           Matabeleland South  
6923           Matabeleland South  

[6924 rows x 5 columns]

#### Create the final table

In [ ]:
%%bigquery
create or replace table air_travel_int.Airport as
    select distinct al.llm_icao as icao, a.iata, a.name, a.city, al.llm_state_prov as state_prov, a.country, a.latitude, a.longitude, a.timezone_delta,
        a.daylight_savings_time, a.timezone_name, a.type, a.source, 'openflights,llm' as _data_source, a._load_time
    from air_travel_stg.airports a join air_travel_tmp.airport_llm al
    on a.name = al.name and a.country = al.country
    where a.iata is not null
    and al.llm_icao is not null

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
select * from air_travel_int.Airport
limit 10

Query is running:   0%|          |

Downloading:   0%|          |

icao iata                               name             city  \
0  KIRT  IKR            Kirtland Air Force Base  Kirtland A.f.b.   
1  SBRG  RIG                         Rio Grande       Rio Grande   
2  KSPS  S42         Springer Municipal Airport         Springer   
3  K55A  6Y9      Prickett-Grooms Field Airport           Sidnaw   
4  EBCV  ZYZ  Antwerpen-Berchem Railway Station        Antwerpen   
5  HSDA  ADV                   Ed Daein Airport         Ed Daein   
6  URRR  RVI              Rostov-on-Don Airport    Rostov-on-Don   
7  KHRI  3O8                       Harris Ranch         Coalinga   
8  SNMC  CMC                            Camocim          Camocim   
9  WHDD  LAH               Oesman Sadik Airport           Labuha   

                          state_prov        country   latitude   longitude  \
0                         New Mexico  United States  35.040222 -106.609194   
1                  Rio Grande do Sul         Brazil -32.082617  -52.166542   
2                         New Mexico  United States  36.331522 -104.617851   
3                          Tennessee  United States  46.508653  -88.705847   
4  Antwerp Province, Flanders Region        Belgium  51.199167    4.433056   
5                       South Darfur          Sudan  11.403611   26.119167   
6                      Rostov Oblast         Russia  47.258300   39.818300   
7                         California  United States  36.248111 -120.238472   
8                              Ceará         Brazil  -2.916667  -40.833332   
9                       North Maluku      Indonesia  -0.637344  127.500750   

   timezone_delta daylight_savings_time      timezone_name     type  source  \
0              -7                     A     America/Denver  airport  Legacy   
1              -3                     S  America/Sao_Paulo  unknown  Legacy   
2              -6                     A               None     None    None   
3              -4                     A               None     None    None   
4               1                     E               None     None    None   
5               2                     N               None     None    None   
6               3                     N               None     None    None   
7              -8                     A               None     None    None   
8              -3                     N               None     None    None   
9               9                     N               None     None    None   

       data_source                       _load_time  
0  openflights,llm 2025-09-05 17:06:39.719594+00:00  
1  openflights,llm 2025-09-05 17:06:39.719594+00:00  
2  openflights,llm 2025-09-05 17:06:39.719594+00:00  
3  openflights,llm 2025-09-05 17:06:39.719594+00:00  
4  openflights,llm 2025-09-05 17:06:39.719594+00:00  
5  openflights,llm 2025-09-05 17:06:39.719594+00:00  
6  openflights,llm 2025-09-05 17:06:39.719594+00:00  
7  openflights,llm 2025-09-05 17:06:39.719594+00:00  
8  openflights,llm 2025-09-05 17:06:39.719594+00:00  
9  openflights,llm 2025-09-05 17:06:39.719594+00:00

#### Check the primary key constraint

In [ ]:
%%bigquery
select icao, count(*) as duplicates
from air_travel_int.Airport
group by icao
having count(*) > 1
order by count(*) desc

Query is running:   0%|          |

Downloading:   0%|          |

icao  duplicates
0     N/A          14
1    OEPA          13
2    EGPC          10
3    PACH           9
4    UUDD           9
..    ...         ...
873   ZQE           2
874  KSUN           2
875  K6A3           2
876  EDSF           2
877  SWOC           2

[878 rows x 2 columns]

In [ ]:
%%bigquery
select icao, iata, name, count(*) as duplicates
from air_travel_int.Airport
group by icao, iata, name
having count(*) > 1
order by count(*) desc

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [icao, iata, name, duplicates]
Index: []

###### This means that we can narrow down the search space to icao, iata, and name (since we don't have any duplicates where all 3 fields are the same)

##### TL;DR: Primary key constraint does not hold, need to identify and remove duplicates

In [ ]:
%%bigquery
select *
from air_travel_int.Airport
where icao in
  (select icao
  from air_travel_int.Airport
  group by icao
  having count(*) > 1)
order by icao
limit 10

Query is running:   0%|          |

Downloading:   0%|          |

icao iata                            name               city  \
0   জন্যও   KIA  Kaieteur International Airport     Kaieteur Falls   
1   জন্যও   KAI  Kaieteur International Airport           Kaieteur   
2      1G4  1G4       Grand Canyon West Airport      Peach Springs   
3      1G4  GCW       Grand Canyon West Airport  Grand Canyon West   
4      3W2  BYW          Blakely Island Airport     Blakely Island   
5      3W2  3W2              Put-in-Bay Airport         Put-in-Bay   
6     AGGO  RNL          Rennell/Tingoa Airport     Rennell Island   
7     AGGO  MUA                   Munda Airport              Munda   
8     AYEL  BN1                         Bellona            Bellona   
9     AYEL  BNY                         Bellona            Bellona   

         state_prov          country   latitude   longitude  timezone_delta  \
0   Potaro-Siparuni           Guyana   5.163333  -59.483333              -4   
1   Potaro-Siparuni           Guyana   5.172755  -59.491482              -4   
2           Arizona    United States  35.899904 -113.815674              -7   
3           Arizona    United States  35.592500 -113.485900              -7   
4        Washington    United States  48.560250 -122.802430              -8   
5              Ohio    United States  41.352100  -82.497000              -5   
6  Rennell Province  Solomon Islands -11.533900  160.063004              11   
7  Western Province  Solomon Islands  -8.327970  157.263000              11   
8           Bellona  Solomon Islands  15.981667  -11.300000               0   
9           Bellona  Solomon Islands -11.302000  159.800000              11   

  daylight_savings_time        timezone_name     type       source  \
0                     U       America/Guyana  airport         User   
1                     U       America/Guyana  airport  OurAirports   
2                     A      America/Phoenix  airport         User   
3                     U      America/Phoenix  airport         User   
4                     A  America/Los_Angeles  airport         User   
5                     A     America/New_York  airport         User   
6                     U  Pacific/Guadalcanal  airport  OurAirports   
7                     U  Pacific/Guadalcanal  airport  OurAirports   
8                     U    Africa/Nouakchott  unknown         User   
9                     U  Pacific/Guadalcanal  unknown         User   

       data_source                       _load_time  
0  openflights,llm 2025-09-05 17:06:39.719594+00:00  
1  openflights,llm 2025-09-05 17:06:39.719594+00:00  
2  openflights,llm 2025-09-05 17:06:39.719594+00:00  
3  openflights,llm 2025-09-05 17:06:39.719594+00:00  
4  openflights,llm 2025-09-05 17:06:39.719594+00:00  
5  openflights,llm 2025-09-05 17:06:39.719594+00:00  
6  openflights,llm 2025-09-05 17:06:39.719594+00:00  
7  openflights,llm 2025-09-05 17:06:39.719594+00:00  
8  openflights,llm 2025-09-05 17:06:39.719594+00:00  
9  openflights,llm 2025-09-05 17:06:39.719594+00:00

#### Perform "fuzzy" dedup to remove duplicate copies of the same airport

##### For all the duplicate records in the table:
1.   Create a temp table in the `[your_domain]_tmp` dataset
2.   Create vector embeddings on the fields `(icao, iata, name)`.
3.   Use the language model to infer the values for the same fields `(icao, iata, name)`, given a list of icao codes
4.   Create vector embeddings of the language model's results
5.   Cluster the embeddings to find the most similar airports using the [vector_search()](https://cloud.google.com/bigquery/docs/reference/standard-sql/search_functions#vector_search) function
6.   Remove all the duplicates from the final table except for the most similar matches



###### Step 1

In [ ]:
%%bigquery
create or replace table air_travel_tmp.airport_duplicates as
  select * from air_travel_int.Airport
  where icao in
    (select icao
     from air_travel_int.Airport
     group by icao
     having count(*) > 1)

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
select *
from air_travel_tmp.airport_duplicates
order by icao

Query is running:   0%|          |

Downloading:   0%|          |

icao iata                                name  \
0              জন্যও   KAI      Kaieteur International Airport   
1              জন্যও   KIA      Kaieteur International Airport   
2                 1G4  GCW           Grand Canyon West Airport   
3                 1G4  1G4           Grand Canyon West Airport   
4                 3W2  BYW              Blakely Island Airport   
...               ...  ...                                 ...   
2204             null  KEZ  Kelani River-Peliyagoda Waterdrome   
2205             null  KHX                   Savannah Airstrip   
2206             null  QQP                  Paddington Station   
2207  ওয়েব অনুসন্ধান  KIA      Kaieteur International Airport   
2208  ওয়েব অনুসন্ধান  KAI      Kaieteur International Airport   

                   city                  state_prov         country  \
0              Kaieteur             Potaro-Siparuni          Guyana   
1        Kaieteur Falls             Potaro-Siparuni          Guyana   
2     Grand Canyon West                     Arizona   United States   
3         Peach Springs                     Arizona   United States   
4        Blakely Island                  Washington   United States   
...                 ...                         ...             ...   
2204            Colombo  Kelaniya, Gampaha District       Sri Lanka   
2205             Kihihi                        null          Uganda   
2206             London                        null  United Kingdom   
2207     Kaieteur Falls             ওয়েব অনুসন্ধান          Guyana   
2208           Kaieteur             ওয়েব অনুসন্ধান          Guyana   

       latitude   longitude  timezone_delta daylight_savings_time  \
0      5.172755  -59.491482              -4                     U   
1      5.163333  -59.483333              -4                     U   
2     35.592500 -113.485900              -7                     U   
3     35.899904 -113.815674              -7                     A   
4     48.560250 -122.802430              -8                     A   
...         ...         ...             ...                   ...   
2204   6.967464   79.881972            <NA>                     N   
2205  -0.719500   29.700000               3                     N   
2206  51.515833   -0.176111               0                     E   
2207   5.163333  -59.483333              -4                     U   
2208   5.172755  -59.491482              -4                     U   

            timezone_name     type       source      data_source  \
0          America/Guyana  airport  OurAirports  openflights,llm   
1          America/Guyana  airport         User  openflights,llm   
2         America/Phoenix  airport         User  openflights,llm   
3         America/Phoenix  airport         User  openflights,llm   
4     America/Los_Angeles  airport         User  openflights,llm   
...                   ...      ...          ...              ...   
2204         Asia/Colombo  unknown         User  openflights,llm   
2205                 None     None         None  openflights,llm   
2206        Europe/London  station         User  openflights,llm   
2207       America/Guyana  airport         User  openflights,llm   
2208       America/Guyana  airport  OurAirports  openflights,llm   

                           _load_time  
0    2025-09-05 17:06:39.719594+00:00  
1    2025-09-05 17:06:39.719594+00:00  
2    2025-09-05 17:06:39.719594+00:00  
3    2025-09-05 17:06:39.719594+00:00  
4    2025-09-05 17:06:39.719594+00:00  
...                               ...  
2204 2025-09-05 17:06:39.719594+00:00  
2205 2025-09-05 17:06:39.719594+00:00  
2206 2025-09-05 17:06:39.719594+00:00  
2207 2025-09-05 17:06:39.719594+00:00  
2208 2025-09-05 17:06:39.719594+00:00  

[2209 rows x 15 columns]

###### Step 2

In [ ]:
%%bigquery
create or replace table air_travel_tmp.airport_duplicates_embeddings as
  select icao, iata, name, ml_generate_embedding_result as embedding
  from
    ML.GENERATE_EMBEDDING(
      model air_travel_model.embedding_model,
      (select icao, iata, name, concat(icao, ',', iata, ',', name) as content
       from air_travel_tmp.airport_duplicates),
      struct(true as flatten_json_output, 'SEMANTIC_SIMILARITY' as task_type)
    )

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
select *
from air_travel_tmp.airport_duplicates_embeddings
limit 10

Query is running:   0%|          |

Downloading:   0%|          |

icao iata                            name  \
0   জন্যও   KIA  Kaieteur International Airport   
1   জন্যও   KAI  Kaieteur International Airport   
2      1G4  GCW       Grand Canyon West Airport   
3      1G4  1G4       Grand Canyon West Airport   
4      3W2  BYW          Blakely Island Airport   
5      3W2  3W2              Put-in-Bay Airport   
6     AGGO  RNL          Rennell/Tingoa Airport   
7     AGGO  MUA                   Munda Airport   
8     AYEL  BN1                         Bellona   
9     AYEL  BNY                         Bellona   

                                           embedding  
0  [-0.013749584555625916, -0.0062225437723100185...  
1  [-0.014796041883528233, -0.0076795704662799835...  
2  [-0.04935675486922264, 0.020620359107851982, -...  
3  [-0.05121694132685661, 0.01426841039210558, -0...  
4  [-0.07072301208972931, 0.039830729365348816, -...  
5  [-0.030567234382033348, 0.0380619615316391, -0...  
6  [-0.05850043147802353, -0.0006740207318216562,...  
7  [-0.03211420774459839, 0.009106386452913284, -...  
8  [-0.02019703947007656, -0.0007735438994131982,...  
9  [-0.031379491090774536, -0.0014326460659503937...

###### Step 3

In [ ]:
%%bigquery
create or replace table air_travel_tmp.airport_inference_results as
  with airport_tmp as (
    select icao,
      AI.GENERATE(
        ('What are the iata code and name of the airport that has the icao code of ', icao, '?'),
        connection_id => 'us-central1.vertex-ai-connection',
        endpoint => 'gemini-2.5-flash-lite',
        model_params => JSON '{"generation_config":{"thinking_config": {"thinking_budget": 0}}, "tools": [{"googleSearch": {}}]}',
        output_schema => 'iata STRING, name STRING') as llm_response
    from (select distinct icao from air_travel_tmp.airport_duplicates)
  )
select icao, llm_response.iata as iata, llm_response.name as name
from airport_tmp

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
select * from air_travel_tmp.airport_inference_results

Query is running:   0%|          |

Downloading:   0%|          |

icao  iata                                               name
0    SVVG  None  Usimac Airport - Puerto Ordaz International Ai...
1    WIMK  None          Sultan Iskandarmuda International Airport
2    FWKI  None  Kikwit Airport, Kikwit, Democratic Republic of...
3    YGDH  None                                     Yagari Airport
4    AYLO  None             Los Cerrillos Airport, Santiago, Chile
..    ...   ...                                                ...
873  GMFK   CMN                   Mohammed V International Airport
874  PAKM   ???                                            Unknown
875  WIOO   XXX                                            Unknown
876  ZBUH  ZBUH                                            Unknown
877  ZUCK   ZZZ                                            Unknown

[878 rows x 3 columns]

###### Step 4

In [ ]:
%%bigquery
create or replace table air_travel_tmp.airport_inference_results_embeddings as
  select icao, iata, name, ml_generate_embedding_result as embedding
  from
    ML.GENERATE_EMBEDDING(
      model air_travel_model.embedding_model,
      (select icao, iata, name, concat(icao, ',', iata, ',', name) as content
       from air_travel_tmp.airport_inference_results
       where iata is not null
       and name != 'Unknown'),
       struct(true as flatten_json_output, 'SEMANTIC_SIMILARITY' as task_type)
    )

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
select *
from air_travel_tmp.airport_inference_results_embeddings
limit 10

Query is running:   0%|          |

Downloading:   0%|          |

icao iata                                name  \
0   3W2  3W2                      Spiker Airport   
1   K70   70                     Mullins Airport   
2  MYAB  AAB                               Araba   
3  EDAC  AAC       El Alto International Airport   
4  HAAB  AAD                    Adiyaman Airport   
5  FALA  AAL                     Aalborg Airport   
6  HAAM  AAM  Malam A Minu International Airport   
7  EDAM  AAM                      Ampara Airport   
8  WABD  AAM                               Adamu   
9  WAML  AAM                            Adhamiya   

                                           embedding  
0  [-0.02818993292748928, 0.031042300164699554, -...  
1  [0.02146093361079693, 0.0042467862367630005, -...  
2  [-0.0270424485206604, 0.01217491365969181, -0....  
3  [-0.024240558966994286, 0.0242815800011158, -0...  
4  [-0.04677737131714821, 0.003668458666652441, -...  
5  [-0.0012524031335487962, 0.049164991825819016,...  
6  [-0.00044116683420725167, 0.005052466411143541...  
7  [-0.02059738151729107, 0.016418904066085815, -...  
8  [-0.051406439393758774, -0.018702514469623566,...  
9  [-0.056495171040296555, -0.020243126899003983,...

###### Step 5

In [ ]:
%%bigquery
select base.icao as base_icao, base.iata as base_iata, base.name as base_name,
  query.icao as query_icao, query.iata as query_iata, query.name as query_name,
  distance
from
  vector_search(
    table air_travel_tmp.airport_duplicates_embeddings, -- this is the base
    'embedding',
    table air_travel_tmp.airport_inference_results_embeddings, -- this is the query
    'embedding',
    top_k => 1,
    distance_type => 'COSINE')
where query.icao = base.icao
order by distance

Query is running:   0%|          |

Downloading:   0%|          |

base_icao base_iata                                 base_name query_icao  \
0        PGUM       GUM  Antonio B. Won Pat International Airport       PGUM   
1        EBBR       BRU                          Brussels Airport       EBBR   
2        NZWN       WLG          Wellington International Airport       NZWN   
3        OMDW       DWC          Al Maktoum International Airport       OMDW   
4        EGJJ       JER                            Jersey Airport       EGJJ   
..        ...       ...                                       ...        ...   
452      SPRO       NZC               Maria Reiche Neuman Airport       SPRO   
453      VTUI       SNO                      Sakon Nakhon Airport       VTUI   
454      KMPN       MMI                     McMinn County Airport       KMPN   
455      MPCE       CTD                 Alonso Valderrama Airport       MPCE   
456      RODR       TRA                            Tarama Airport       RODR   

    query_iata                                query_name  distance  
0          GUM  Antonio B. Won Pat International Airport  0.000000  
1          BRU                          Brussels Airport  0.000000  
2          WLG          Wellington International Airport  0.000000  
3          DWC          Al Maktoum International Airport  0.000000  
4          JER                            Jersey Airport  0.000000  
..         ...                                       ...       ...  
452        SPR                                 Spreckels  0.299260  
453        XXX                                 Not found  0.310442  
454        MPN                            Julian A. Diaz  0.312123  
455        PLC                                  Albrook   0.312451  
456        RDR                                     Reyes  0.326727  

[457 rows x 7 columns]

###### Look at the results to determine a reasonable similarity threshold. This will be dataset specific. Mine is < 0.08

In [ ]:
%%bigquery
create or replace table air_travel_tmp.airport_vector_search_results as
  select base.icao as base_icao, base.iata as base_iata, base.name as base_name,
    query.icao as query_icao, query.iata as query_iata, query.name as query_name,
    distance
  from
    vector_search(
      table air_travel_tmp.airport_duplicates_embeddings, -- this is the base (i.e what's in the Airport table)
      'embedding',
      table air_travel_tmp.airport_inference_results_embeddings, -- this is the query (i.e. results from LLM inference)
      'embedding',
      top_k => 1,
      distance_type => 'COSINE')
  where query.icao = base.icao
  order by distance

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
select * from air_travel_tmp.airport_vector_search_results
where distance < 0.08
order by distance

Query is running:   0%|          |

Downloading:   0%|          |

base_icao base_iata                        base_name query_icao  \
0        EGLL       LHR          London Heathrow Airport       EGLL   
1        KSBA       SBA  Santa Barbara Municipal Airport       KSBA   
2        KHVN       HVN          Tweed New Haven Airport       KHVN   
3        KMOB       MOB          Mobile Regional Airport       KMOB   
4        KJEF       JEF  Jefferson City Memorial Airport       KJEF   
..        ...       ...                              ...        ...   
135      PAKN       AUK                 Alakanuk Airport       PAKN   
136      SBPS       BPS             Porto Seguro Airport       SBPS   
137      NGFU       FUN   Funafuti International Airport       NGFU   
138      LFOB       BOU                  Bourges Airport       LFOB   
139      BIRK       RKV                Reykjavik Airport       BIRK   

    query_iata                                        query_name  distance  
0          LHR                           London Heathrow Airport  0.000000  
1          SBA                   Santa Barbara Municipal Airport  0.000000  
2          HVN                           Tweed New Haven Airport  0.000000  
3          MOB                           Mobile Regional Airport  0.000000  
4          JEF                   Jefferson City Memorial Airport  0.000000  
..         ...                                               ...       ...  
135        AKN                                Unalakleet Airport  0.075687  
136        PSA  Porto Alegre/Salgado Filho International Airport  0.076958  
137        FUA               Fua Muliolefo International Airport  0.077866  
138        OBS                            Brest Bretagne Airport  0.078091  
139        RKV                                         Reykjavik  0.078836  

[140 rows x 7 columns]

###### Step 6

In [ ]:
%%bigquery
select count(*) from air_travel_int.Airport

Query is running:   0%|          |

Downloading:   0%|          |

f0_
0  6977

In [ ]:
%%bigquery
delete from air_travel_int.Airport
where icao in (select distinct icao from air_travel_tmp.airport_duplicates)

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
select count(*) from air_travel_int.Airport

Query is running:   0%|          |

Downloading:   0%|          |

f0_
0  4768

In [ ]:
%%bigquery
select * from air_travel_tmp.airport_duplicates
  where concat(icao, ',', iata, ',', name) in
      (select concat(base_icao, ',', base_iata, ',', base_name)
       from air_travel_tmp.airport_vector_search_results
       where distance < 0.08)

Query is running:   0%|          |

Downloading:   0%|          |

icao iata                                      name  \
0    KPOU  POU                   Dutchess County Airport   
1    LTFM  IST                          Istanbul Airport   
2    YWNG  WGT                        Wangaratta Airport   
3    HECA  CAI               Cairo International Airport   
4    GMMN  CMN          Mohammed V International Airport   
..    ...  ...                                       ...   
135  NZQN  ZQN          Queenstown International Airport   
136  NZWN  WLG          Wellington International Airport   
137  NGFU  FUN            Funafuti International Airport   
138  PGUM  GUM  Antonio B. Won Pat International Airport   
139  AYWK  WWK               Wewak International Airport   

                         city           state_prov           country  \
0                Poughkeepsie             New York     United States   
1                    Istanbul    Istanbul Province            Turkey   
2                        None             Victoria         Australia   
3                       Cairo                Cairo             Egypt   
4                  Casablanca    Casablanca-Settat           Morocco   
..                        ...                  ...               ...   
135  Queenstown International                Otago       New Zealand   
136                Wellington           Wellington       New Zealand   
137                  Funafuti               Tuvalu            Tuvalu   
138                     Agana                 Guam              Guam   
139                     Wewak  East Sepik Province  Papua New Guinea   

      latitude   longitude  timezone_delta daylight_savings_time  \
0    41.626598  -73.884201            <NA>                    \N   
1    41.275278   28.751944               3                     E   
2   -36.415798  146.307007            <NA>                    \N   
3    30.121901   31.405600               2                     U   
4    33.367500   -7.589970               0                     N   
..         ...         ...             ...                   ...   
135 -45.021099  168.738998              12                     Z   
136 -41.327202  174.804993              12                     Z   
137  -8.525000  179.195999              12                     U   
138  13.483400  144.796005              10                     U   
139  -3.583830  143.669006              10                     U   

            timezone_name     type       source      data_source  \
0                    None  airport  OurAirports  openflights,llm   
1                    None  airport  OurAirports  openflights,llm   
2                    None  airport  OurAirports  openflights,llm   
3            Africa/Cairo  airport  OurAirports  openflights,llm   
4       Africa/Casablanca  airport  OurAirports  openflights,llm   
..                    ...      ...          ...              ...   
135      Pacific/Auckland  airport  OurAirports  openflights,llm   
136      Pacific/Auckland  airport  OurAirports  openflights,llm   
137      Pacific/Funafuti  airport  OurAirports  openflights,llm   
138          Pacific/Guam  airport  OurAirports  openflights,llm   
139  Pacific/Port_Moresby  airport  OurAirports  openflights,llm   

                          _load_time  
0   2025-09-05 17:06:39.719594+00:00  
1   2025-09-05 17:06:39.719594+00:00  
2   2025-09-05 17:06:39.719594+00:00  
3   2025-09-05 17:06:39.719594+00:00  
4   2025-09-05 17:06:39.719594+00:00  
..                               ...  
135 2025-09-05 17:06:39.719594+00:00  
136 2025-09-05 17:06:39.719594+00:00  
137 2025-09-05 17:06:39.719594+00:00  
138 2025-09-05 17:06:39.719594+00:00  
139 2025-09-05 17:06:39.719594+00:00  

[140 rows x 15 columns]

In [ ]:
%%bigquery
insert into air_travel_int.Airport
  select * from air_travel_tmp.airport_duplicates
  where concat(icao, ',', iata, ',', name) in
      (select concat(base_icao, ',', base_iata, ',', base_name)
       from air_travel_tmp.airport_vector_search_results
       where distance < 0.08)


Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

###### Check results

In [ ]:
%%bigquery
select * from air_travel_int.Airport
where icao in (select base_icao from air_travel_tmp.airport_vector_search_results where distance < 0.08)

Query is running:   0%|          |

Downloading:   0%|          |

icao iata                                      name  \
0    YWNG  WGT                        Wangaratta Airport   
1    KPOU  POU                   Dutchess County Airport   
2    OIIE  IKA       Imam Khomeini International Airport   
3    YPOR  PUG                      Port Augusta Airport   
4    PADK  ADK                              Adak Airport   
..    ...  ...                                       ...   
135  PGUM  GUM  Antonio B. Won Pat International Airport   
136  AYWK  WWK               Wewak International Airport   
137  NZWN  WLG          Wellington International Airport   
138  NZQN  ZQN          Queenstown International Airport   
139  NGFU  FUN            Funafuti International Airport   

                         city           state_prov           country  \
0                        None             Victoria         Australia   
1                Poughkeepsie             New York     United States   
2                      Tehran      Tehran Province              Iran   
3                      Argyle      South Australia         Australia   
4                 Adak Island               Alaska     United States   
..                        ...                  ...               ...   
135                     Agana                 Guam              Guam   
136                     Wewak  East Sepik Province  Papua New Guinea   
137                Wellington           Wellington       New Zealand   
138  Queenstown International                Otago       New Zealand   
139                  Funafuti               Tuvalu            Tuvalu   

      latitude   longitude  timezone_delta daylight_savings_time  \
0   -36.415798  146.307007            <NA>                    \N   
1    41.626598  -73.884201            <NA>                    \N   
2    35.416100   51.152199            <NA>                     E   
3   -32.506901  137.716995            <NA>                     O   
4    51.877998 -176.645996             -10                     A   
..         ...         ...             ...                   ...   
135  13.483400  144.796005              10                     U   
136  -3.583830  143.669006              10                     U   
137 -41.327202  174.804993              12                     Z   
138 -45.021099  168.738998              12                     Z   
139  -8.525000  179.195999              12                     U   

            timezone_name     type       source      data_source  \
0                    None  airport  OurAirports  openflights,llm   
1                    None  airport  OurAirports  openflights,llm   
2             Asia/Tehran  airport  OurAirports  openflights,llm   
3      Australia/Adelaide  airport  OurAirports  openflights,llm   
4            America/Adak  airport  OurAirports  openflights,llm   
..                    ...      ...          ...              ...   
135          Pacific/Guam  airport  OurAirports  openflights,llm   
136  Pacific/Port_Moresby  airport  OurAirports  openflights,llm   
137      Pacific/Auckland  airport  OurAirports  openflights,llm   
138      Pacific/Auckland  airport  OurAirports  openflights,llm   
139      Pacific/Funafuti  airport  OurAirports  openflights,llm   

                          _load_time  
0   2025-09-05 17:06:39.719594+00:00  
1   2025-09-05 17:06:39.719594+00:00  
2   2025-09-05 17:06:39.719594+00:00  
3   2025-09-05 17:06:39.719594+00:00  
4   2025-09-05 17:06:39.719594+00:00  
..                               ...  
135 2025-09-05 17:06:39.719594+00:00  
136 2025-09-05 17:06:39.719594+00:00  
137 2025-09-05 17:06:39.719594+00:00  
138 2025-09-05 17:06:39.719594+00:00  
139 2025-09-05 17:06:39.719594+00:00  

[140 rows x 15 columns]

In [ ]:
%%bigquery
select count(*) from air_travel_int.Airport

Query is running:   0%|          |

Downloading:   0%|          |

f0_
0  4908

##### Recheck primary key constraint

In [ ]:
%%bigquery
select icao, count(*)
from air_travel_int.Airport
group by icao
having count(*) > 1

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [icao, f0_]
Index: []

##### Fix the foreign key (country). Instead of the country name, it should be the iso code

In [ ]:
%%bigquery
select count(distinct country)
from air_travel_int.Airport
where country not in (select name from air_travel_int.Country)

Query is running:   0%|          |

Downloading:   0%|          |

f0_
0   14

##### We have 14 unique countries which are orphan, resolve by mapping to their iso code

In [ ]:
%%bigquery
create or replace table air_travel_tmp.airport_countries_iso_code as
  with orphan_countries as (
    select distinct country as airport_country_name
    from air_travel_int.Airport
    where country not in (select name from air_travel_int.Country)
  ),
  airport_country_tmp as (
    select airport_country_name,
      AI.GENERATE(
        ('What is the iso code for the country ', airport_country_name, '? If it does not have an iso code, return None.'),
        connection_id => 'us-central1.vertex-ai-connection',
        endpoint => 'gemini-2.5-flash-lite',
        model_params => JSON '{"generation_config":{"thinking_config": {"thinking_budget": 0}}, "tools": [{"googleSearch": {}}]}',
        output_schema => 'iso_code STRING') as llm_response
    from orphan_countries
  )
select airport_country_name, llm_response.iso_code as mapped_iso_code
from airport_country_tmp

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
select * from air_travel_tmp.airport_countries_iso_code
order by airport_country_name

Query is running:   0%|          |

Downloading:   0%|          |

airport_country_name mapped_iso_code
0                              Burma              MM
1                         Cape Verde              CV
2                Congo (Brazzaville)             COG
3                   Congo (Kinshasa)              CD
4                         East Timor             TLS
5                      Faroe Islands             FRO
6                         Kyrgyzstan             KGZ
7                              Macau              MO
8                         Micronesia             FSM
9                        Saint Lucia              LC
10         Saint Pierre and Miquelon              PM
11  Saint Vincent and the Grenadines              VC
12                         Swaziland              SZ
13                    Virgin Islands              VI

##### Recreate the final table with the iso_code, which will be the foreign key. For now keep the country name in the table so that we can use it to map the orphan country records

In [ ]:
%%bigquery
create or replace table air_travel_int.Airport as
  select a.icao, a.iata, a.name, a.city, a.state_prov, a.country as country_name, c.iso_code as country_code,
    a.latitude, a.longitude, a.timezone_delta, a.daylight_savings_time, a.timezone_name,
    a.type, a.source, a.data_source, a._load_time
  from air_travel_int.Airport a left join air_travel_int.Country c
  on a.country = c.name

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
select * from air_travel_int.Airport
limit 10

Query is running:   0%|          |

Downloading:   0%|          |

icao iata               name         city          state_prov  \
0   OAGN  GZI     Ghazni Airport       Ghazni     Ghazni Province   
1   OAFR  FAH      Farah Airport        Farah      Farah Province   
2   OAIX  OAI    Bagram Air Base        Kabul     Parwan Province   
3   OAKS  KHT      Khost Airport        Khost      Khost Province   
4   OAHE  HEA      Herat Airport        Herat      Herat Province   
5   OAHN  UND     Konduz Airport       Kunduz              Kondoz   
6   OAAJ  JAA  Jalalabad Airport    Jalalabad  Nangarhar Province   
7   OABN  BIN    Bamiyan Airport       Bamyan    Bamiyan Province   
8   OABT  BST       Bost Airport  Lashkar Gah    Helmand Province   
9  OA_ZJ  ZAJ     Zaranj Airport       Zaranj              Nimruz   

  country_name country_code   latitude  longitude  timezone_delta  \
0  Afghanistan           AF  33.531200  68.412903            <NA>   
1  Afghanistan           AF  32.367001  62.182999            <NA>   
2  Afghanistan           AF  34.946098  69.264999            <NA>   
3  Afghanistan           AF  33.333401  69.952003            <NA>   
4  Afghanistan           AF  34.209999  62.228298            <NA>   
5  Afghanistan           AF  36.665100  68.910797            <NA>   
6  Afghanistan           AF  34.399799  70.498596            <NA>   
7  Afghanistan           AF  34.817001  67.817001            <NA>   
8  Afghanistan           AF  31.559700  64.364998            <NA>   
9  Afghanistan           AF  30.972222  61.865833            <NA>   

  daylight_savings_time timezone_name     type       source      data_source  \
0                     N          None  airport  OurAirports  openflights,llm   
1                     N          None  airport  OurAirports  openflights,llm   
2                     U    Asia/Kabul  airport  OurAirports  openflights,llm   
3                     N    Asia/Kabul  airport  OurAirports  openflights,llm   
4                     U    Asia/Kabul  airport  OurAirports  openflights,llm   
5                     U    Asia/Kabul  airport  OurAirports  openflights,llm   
6                     U    Asia/Kabul  airport  OurAirports  openflights,llm   
7                     N    Asia/Kabul  airport  OurAirports  openflights,llm   
8                     U    Asia/Kabul  airport  OurAirports  openflights,llm   
9                     U    Asia/Kabul  airport  OurAirports  openflights,llm   

                        _load_time  
0 2025-09-05 17:06:39.719594+00:00  
1 2025-09-05 17:06:39.719594+00:00  
2 2025-09-05 17:06:39.719594+00:00  
3 2025-09-05 17:06:39.719594+00:00  
4 2025-09-05 17:06:39.719594+00:00  
5 2025-09-05 17:06:39.719594+00:00  
6 2025-09-05 17:06:39.719594+00:00  
7 2025-09-05 17:06:39.719594+00:00  
8 2025-09-05 17:06:39.719594+00:00  
9 2025-09-05 17:06:39.719594+00:00

In [ ]:
%%bigquery
update air_travel_int.Airport a
  set country_code =
    (select mapped_iso_code
    from air_travel_tmp.airport_countries_iso_code i
    where a.country_name = i.airport_country_name)
  where country_code is null

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
select * from air_travel_int.Airport
limit 10

Query is running:   0%|          |

Downloading:   0%|          |

icao iata                                  name                 city  \
0    OMSJ  SHJ         Sharjah International Airport              Sharjah   
1    OMK4  ZDY                         Dalma Airport         Dalma Island   
2    OMAM  DHF                    Al Dhafra Air Base            Abu Dhabi   
3  OM-BJS  XSB                  Sir Bani Yas Airport  Sir Bani Yas Island   
4    OMAA  AUH       Abu Dhabi International Airport            Abu Dhabi   
5    OMFJ  FJR        Fujairah International Airport             Fujeirah   
6    OMRK  RKT  Ras Al Khaimah International Airport       Ras Al Khaimah   
7    OMDN  XNB                    Etihad Travel Mall                Dubai   
8    OMAL  AAN          Al Ain International Airport               Al Ain   
9    OMDB  DXB           Dubai International Airport                Dubai   

       state_prov          country_name country_code   latitude  longitude  \
0         Sharjah  United Arab Emirates           AE  25.328600  55.517200   
1       Abu Dhabi  United Arab Emirates           AE  24.503383  52.336053   
2       Abu Dhabi  United Arab Emirates           AE  24.248199  54.547699   
3       Abu Dhabi  United Arab Emirates           AE  24.283611  52.580278   
4       Abu Dhabi  United Arab Emirates           AE  24.433001  54.651100   
5        Fujairah  United Arab Emirates           AE  25.112200  56.324001   
6  Ras Al Khaimah  United Arab Emirates           AE  25.613501  55.938801   
7           Dubai  United Arab Emirates           AE  25.154721  55.226424   
8       Abu Dhabi  United Arab Emirates           AE  24.261700  55.609200   
9           Dubai  United Arab Emirates           AE  25.252800  55.364399   

   timezone_delta daylight_savings_time timezone_name     type       source  \
0               4                     U    Asia/Dubai  airport  OurAirports   
1               4                     U    Asia/Dubai  airport         User   
2               4                     U    Asia/Dubai  airport  OurAirports   
3               4                     U    Asia/Dubai  airport  OurAirports   
4               4                     U    Asia/Dubai  airport  OurAirports   
5               4                     U    Asia/Dubai  airport  OurAirports   
6               4                     U    Asia/Dubai  airport  OurAirports   
7               4                     N    Asia/Dubai  unknown         User   
8               4                     U    Asia/Dubai  airport  OurAirports   
9               4                     U    Asia/Dubai  airport  OurAirports   

       data_source                       _load_time  
0  openflights,llm 2025-09-05 17:06:39.719594+00:00  
1  openflights,llm 2025-09-05 17:06:39.719594+00:00  
2  openflights,llm 2025-09-05 17:06:39.719594+00:00  
3  openflights,llm 2025-09-05 17:06:39.719594+00:00  
4  openflights,llm 2025-09-05 17:06:39.719594+00:00  
5  openflights,llm 2025-09-05 17:06:39.719594+00:00  
6  openflights,llm 2025-09-05 17:06:39.719594+00:00  
7  openflights,llm 2025-09-05 17:06:39.719594+00:00  
8  openflights,llm 2025-09-05 17:06:39.719594+00:00  
9  openflights,llm 2025-09-05 17:06:39.719594+00:00

In [ ]:
%%bigquery
select count(*)
from air_travel_int.Airport
where country_code is null

Query is running:   0%|          |

Downloading:   0%|          |

f0_
0    0

##### Remove the country_name from the table (resolving anomaly type 10 since country_code is now the foreign key)

In [ ]:
%%bigquery
create or replace table air_travel_int.Airport as
  select * except (country_name)
  from air_travel_int.Airport

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
select * from air_travel_int.Airport
limit 10

Query is running:   0%|          |

Downloading:   0%|          |

icao iata                           name              city  \
0  NS-003  TAV                   Ta'u Airport              Ta'u   
1    PCAS  CXI  Cassidy International Airport        Kiritimati   
2    NZMB  MHB                  Mechanics Bay          Auckland   
3    KLXN  L20                     Coal Creek        Coal Creek   
4    AYAP  AMG                         Amboin            Amboin   
5    BGIT  OBY      Ittoqqortoormiit Heliport  Ittoqqortoormiit   
6    LPPD  PDL          João Paulo II Airport     Ponta Delgada   
7    LPGR  GRW               Graciosa Airport   Graciosa Island   
8    LPPI  PIX                   Pico Airport              Pico   
9    LPSJ  SJZ              São Jorge Airport  Sao Jorge Island   

                  state_prov country_code   latitude   longitude  \
0             American Samoa           AS -14.229167 -169.511111   
1               Line Islands           KI   1.986160 -157.350006   
2                   Auckland           NZ -36.846000  174.788000   
3                 Washington           US  65.311336 -143.135452   
4  East New Britain Province           PG  -9.441944  147.218889   
5                 Sermersooq           GL  70.488229  -21.971680   
6                     Azores           PT  37.741199  -25.697901   
7                     Azores           PT  39.092201  -28.029800   
8                     Azores           PT  38.554298  -28.441299   
9                     Azores           PT  38.665501  -28.175800   

   timezone_delta daylight_savings_time         timezone_name     type  \
0             -11                     U                  None     None   
1             -12                     U                  None  airport   
2              13                     Z                  None     None   
3              -1                     A                  None     None   
4              13                     U                  None  unknown   
5              -1                     U  America/Scoresbysund  airport   
6              -1                     E       Atlantic/Azores  airport   
7              -1                     E       Atlantic/Azores  airport   
8              -1                     E       Atlantic/Azores  airport   
9              -1                     E       Atlantic/Azores  airport   

        source      data_source                       _load_time  
0         None  openflights,llm 2025-09-05 17:06:39.719594+00:00  
1  OurAirports  openflights,llm 2025-09-05 17:06:39.719594+00:00  
2         None  openflights,llm 2025-09-05 17:06:39.719594+00:00  
3         None  openflights,llm 2025-09-05 17:06:39.719594+00:00  
4         User  openflights,llm 2025-09-05 17:06:39.719594+00:00  
5  OurAirports  openflights,llm 2025-09-05 17:06:39.719594+00:00  
6  OurAirports  openflights,llm 2025-09-05 17:06:39.719594+00:00  
7  OurAirports  openflights,llm 2025-09-05 17:06:39.719594+00:00  
8  OurAirports  openflights,llm 2025-09-05 17:06:39.719594+00:00  
9  OurAirports  openflights,llm 2025-09-05 17:06:39.719594+00:00

#### Create the TSA_Traffic table (resolving anomaly type 9)

In [ ]:
%%bigquery
select *
from air_travel_stg.tsa_traffic
where event_date is not null
and event_hour is not null
limit 10

Query is running:   0%|          |

Downloading:   0%|          |

event_date  event_hour airport_code                  airport_name  \
0  2021-11-22           4         None                          None   
1  2023-02-20         500          LAX     Los Angeles International   
2  2023-02-20         400          ITH               Ithaca Regional   
3  2023-02-20         500          ITH               Ithaca Regional   
4  2023-02-20         400          ORD  Chicago O'Hare International   
5  2023-02-20         400          RAP           Rapid City Regional   
6  2023-02-20         400          ORD  Chicago O'Hare International   
7  2023-02-20         400          ORD  Chicago O'Hare International   
8  2023-02-20         400          ORD  Chicago O'Hare International   
9  2022-11-28         300          ORD  Chicago O'Hare International   

  airport_city airport_state security_checkpoint  total_traffic _data_source  \
0         None          None                None           <NA>          tsa   
1         None          None                None           <NA>          tsa   
2       Ithaca            NY                0240             54          tsa   
3       Ithaca            NY                0240              2          tsa   
4      Chicago            IL                   1            491          tsa   
5   Rapid City            SD                   1             52          tsa   
6      Chicago            IL                 10A            501          tsa   
7      Chicago            IL                   2            523          tsa   
8      Chicago            IL                   3            182          tsa   
9      Chicago            IL                  4B              7          tsa   

                        _load_time  
0 2025-09-13 17:22:26.134702+00:00  
1 2025-09-13 17:22:26.134702+00:00  
2 2025-09-13 17:22:26.134702+00:00  
3 2025-09-13 17:22:26.134702+00:00  
4 2025-09-13 17:22:26.134702+00:00  
5 2025-09-13 17:22:26.134702+00:00  
6 2025-09-13 17:22:26.134702+00:00  
7 2025-09-13 17:22:26.134702+00:00  
8 2025-09-13 17:22:26.134702+00:00  
9 2025-09-13 17:22:26.134702+00:00

In [ ]:
%%bigquery
select distinct t.event_date, t.event_hour, a.icao as airport_icao, t.security_checkpoint, t.total_traffic,
  t._data_source, t._load_time
from air_travel_int.Airport a join air_travel_stg.tsa_traffic t
on a.iata = t.airport_code
and a.city = t.airport_city
where a.country = 'United States'
and t.event_date is not null
and t.event_hour is not null
and a.icao is not null
and t.security_checkpoint is not null

Query is running:   0%|          |

Downloading:   0%|          |

event_date  event_hour airport_icao          security_checkpoint  \
0    2023-02-20         500         PAFA                     ASAA-FAI   
1    2023-02-20         400         KSAN                CP Terminal 2   
2    2023-02-20         400         KSBA                        SBA01   
3    2022-11-28         300         KFAT                       FAT 01   
4    2022-11-28         200         KSFO  Harvey Milk T1 Checkpoint B   
..          ...         ...          ...                          ...   
577  2023-02-20         400         KCMH                            A   
578  2023-02-20         400         KCMH                            B   
579  2023-02-20         300         KIND                 Checkpoint A   
580  2023-02-20         400         KABE          ABE Main Checkpoint   
581  2023-02-20         500         KBOS                           A1   

     total_traffic _data_source                       _load_time  
0              132          tsa 2025-09-13 17:22:26.134702+00:00  
1              593          tsa 2025-09-13 17:22:26.134702+00:00  
2               62          tsa 2025-09-13 17:22:26.134702+00:00  
3               12          tsa 2025-09-13 17:22:26.134702+00:00  
4               17          tsa 2025-09-13 17:22:26.134702+00:00  
..             ...          ...                              ...  
577            182          tsa 2025-09-13 17:22:26.134702+00:00  
578            421          tsa 2025-09-13 17:22:26.134702+00:00  
579             19          tsa 2025-09-13 17:22:26.134702+00:00  
580             25          tsa 2025-09-13 17:22:26.134702+00:00  
581            521          tsa 2025-09-13 17:22:26.134702+00:00  

[582 rows x 7 columns]

##### Create the final table

In [ ]:
%%bigquery
create or replace table air_travel_int.TSA_Traffic as
  select distinct t.event_date, t.event_hour, a.icao as airport_icao, t.security_checkpoint, t.total_traffic,
    t._data_source, t._load_time
  from air_travel_int.Airport a join air_travel_stg.tsa_traffic t
  on a.iata = t.airport_code
  and a.city = t.airport_city
  where a.country = 'United States'
  and t.event_date is not null
  and t.event_hour is not null
  and a.icao is not null
  and t.security_checkpoint is not null

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
select * from air_travel_int.TSA_Traffic
limit 10

Query is running:   0%|          |

Downloading:   0%|          |

event_date  event_hour airport_icao  security_checkpoint  total_traffic  \
0  2023-02-20           0         KORD                   4B             14   
1  2023-02-20           0         KORD                   7A              1   
2  2023-02-20           0         KABE  ABE Main Checkpoint            120   
3  2023-02-20           0         KMEM         B Checkpoint              1   
4  2022-11-28           0         KEWR                   C1              4   
5  2023-02-20           0         KEWR                 C3-1             24   
6  2023-02-20           0         KEWR                 C3-2              2   
7  2023-02-20           0         KEWR                 C3-3             44   
8  2022-11-28           0         KELP   Central Checkpoint             11   
9  2023-02-20           0         KLGB           Checkpoint              1   

  _data_source                       _load_time  
0          tsa 2025-09-13 17:22:26.134702+00:00  
1          tsa 2025-09-13 17:22:26.134702+00:00  
2          tsa 2025-09-13 17:22:26.134702+00:00  
3          tsa 2025-09-13 17:22:26.134702+00:00  
4          tsa 2025-09-13 17:22:26.134702+00:00  
5          tsa 2025-09-13 17:22:26.134702+00:00  
6          tsa 2025-09-13 17:22:26.134702+00:00  
7          tsa 2025-09-13 17:22:26.134702+00:00  
8          tsa 2025-09-13 17:22:26.134702+00:00  
9          tsa 2025-09-13 17:22:26.134702+00:00

##### Check for primary key fields for uniqueness

In [ ]:
%%bigquery
select event_date, event_hour, airport_icao, security_checkpoint, count(*) as count
from air_travel_int.TSA_Traffic
group by event_date, event_hour, airport_icao, security_checkpoint
having count(*) > 1
order by count(*) desc

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [event_date, event_hour, airport_icao, security_checkpoint, count]
Index: []

##### Check the foreign key field for referential integrity violations

In [ ]:
%%bigquery
select count(*)
from air_travel_int.TSA_Traffic
where airport_icao not in (select icao from air_travel_int.Airport)

Query is running:   0%|          |

Downloading:   0%|          |

f0_
0    0

#### Create the Airport_Review table (resolving anomaly type 9)

In [ ]:
%%bigquery
select *
from air_travel_stg.airport_reviews
limit 10

Query is running:   0%|          |

Downloading:   0%|          |

id  review_thread  airport_id airport_code review_date review_author  \
0   133            106        3483         KDCA  2007-07-18         XingR   
1   138            111        1926         CYTZ  2007-07-18        Bonnie   
2   570            543        4468         LQMO  2007-08-04          None   
3   606            579        1991         CYZD  2007-08-08         david   
4  3371           2885        3622         KJFK  2009-01-30     ianturton   
5  4047           3371       20064         KHMT  2009-07-08          None   
6  5246           3977        4441         LPBJ  2010-02-24          None   
7  5596           4618        1290         CNA9  2010-05-05          None   
8  5920           5076       28324         CST8  2010-06-08          None   
9  8869           6115        1795         CYKZ  2011-07-09         david   

               review_subject  \
0                    Close In   
1   Awesome downtown airport!   
2    Medugorje Mostar Airport   
3          Not open to public   
4                   JKF Sucks   
5                      Better   
6            re: Beja Airport   
7                     Tomvale   
8            What a surprise!   
9  re: A Bigger Small Airport   

                                      review_details  \
0  One of the nation's better airports for the pa...   
1  This is a great airport if you are visiting To...   
2  Mostar airport is the closest destination to M...   
3  This airport is in an ideal location, right in...   
4  This has to be one of the worst airports it ha...   
5  this is really close to my home i like it caus...   
6  Me too.   can,t wait, it will save such a lot ...   
7  It is a PPR airport.  What a pain.  I would us...   
8  I was in Montreal on Sunday 6 June, riding in ...   
9  Reply to @dazuppa: I've never taken instructio...   

             broad_category   sub_category sentiment language  \
0  Transportation & Parking  Accessibility  Positive  English   
1  Transportation & Parking  Accessibility  Positive  English   
2  Transportation & Parking  Accessibility  Positive  English   
3  Transportation & Parking  Accessibility   Neutral  English   
4       Terminal Experience  Accessibility  Negative  English   
5  Transportation & Parking  Accessibility  Positive  English   
6  Transportation & Parking  Accessibility  Positive  English   
7       Terminal Experience  Accessibility  Negative  English   
8  Transportation & Parking  Accessibility  Positive  English   
9  Transportation & Parking  Accessibility  Negative  English   

       _data_source                       _load_time  
0  our-airports,llm 2025-09-19 18:37:01.277997+00:00  
1  our-airports,llm 2025-09-19 18:37:01.277997+00:00  
2  our-airports,llm 2025-09-19 18:37:01.277997+00:00  
3  our-airports,llm 2025-09-19 18:37:01.277997+00:00  
4  our-airports,llm 2025-09-19 18:37:01.277997+00:00  
5  our-airports,llm 2025-09-19 18:37:01.277997+00:00  
6  our-airports,llm 2025-09-19 18:37:01.277997+00:00  
7  our-airports,llm 2025-09-19 18:37:01.277997+00:00  
8  our-airports,llm 2025-09-19 18:37:01.277997+00:00  
9  our-airports,llm 2025-09-19 18:37:01.277997+00:00

##### Recreate the table without the airport_id field since we are standardizing on the icao code and only with the records that join on the Airport table

In [ ]:
%%bigquery
select distinct r.id, r.review_thread, r.review_date, r.review_author,
    r.review_subject, r.review_details, a.icao as airport_icao, r.broad_category, r.sub_category, r.sentiment,
    r.language, r._data_source, r._load_time
from air_travel_stg.airport_reviews r join air_travel_int.Airport a
on a.icao = r.airport_code

Query is running:   0%|          |

Downloading:   0%|          |

id  review_thread review_date review_author  \
0     19963          17322  2014-06-30          None   
1     34873          32245  2018-08-26          None   
2     82473          79829  2020-01-13         david   
3       533            506  2007-07-29         XingR   
4     82690          80047  2020-06-02     sunny2020   
...     ...            ...         ...           ...   
4981    455            428  2007-07-29         Ozguy   
4982   8877            428  2011-07-09  bigjulie_chc   
4983   7970           6812  2011-03-11          None   
4984  24373          21732  2017-03-16          None   
4985  24360          21719  2017-03-15          None   

                                         review_subject  \
0                                             vary good   
1                                                    hi   
2             Ukraine International Airlines Flight 752   
3                                       It's near boats   
4     review about the airport - always preferred to...   
...                                                 ...   
4981                                                CHC   
4982                                            re: CHC   
4983    RNZAF Whenuapai Whenuapai Aviation Sports Club.   
4984                                       (no subject)   
4985                                       (no subject)   

                                         review_details airport_icao  \
0     It's the best airport in IRAN. I think it is v...         OIIE   
1     the designs is not suitable but this is a big ...         OIIE   
2     On 8 January 2020, during a time of military t...         OIIE   
3     Visited here many times when my son was statio...         KSAN   
4     I have visited so many airports but I love the...         KSFO   
...                                                 ...          ...   
4981                   A good airport in a lovely city.         NZCH   
4982           Reply to @Ozguy: Thanx very much, Ozguy!         NZCH   
4983  They have a Great Flying Club, Some great peop...         NZWP   
4984  Here  NEWZEALAND officer  pregnant held  up  f...         NZPP   
4985  POLICE pregnant  held  near  ballikurava  fore...         NZPP   

              broad_category                    sub_category sentiment  \
0        Terminal Experience              Ambience & Comfort  Positive   
1        Terminal Experience              Ambience & Comfort  Negative   
2       Boarding & Departure                 Safety & Health  Negative   
3        Terminal Experience              Ambience & Comfort  Positive   
4        Terminal Experience                   Airport Staff  Positive   
...                      ...                             ...       ...   
4981     Terminal Experience              Ambience & Comfort  Positive   
4982     Terminal Experience                   Miscellaneous  Positive   
4983     Terminal Experience          Amenities & Facilities  Positive   
4984  Security & Immigration  Immigration & Passport Control  Negative   
4985     Terminal Experience                   Miscellaneous   Neutral   

     language      _data_source                       _load_time  
0     English  our-airports,llm 2025-09-19 18:37:01.277997+00:00  
1     English  our-airports,llm 2025-09-19 18:37:01.277997+00:00  
2     English  our-airports,llm 2025-09-19 18:37:01.277997+00:00  
3     English  our-airports,llm 2025-09-19 18:37:01.277997+00:00  
4     English  our-airports,llm 2025-09-19 18:37:01.277997+00:00  
...       ...               ...                              ...  
4981  English  our-airports,llm 2025-09-19 18:37:01.277997+00:00  
4982  English  our-airports,llm 2025-09-19 18:37:01.277997+00:00  
4983  English  our-airports,llm 2025-09-19 18:37:01.277997+00:00  
4984  English  our-airports,llm 2025-09-19 18:37:01.277997+00:00  
4985  English  our-airports,llm 2025-09-19 18:37:01.277997+00:00  

[4986 rows x 13 columns]

##### Create the final table

In [ ]:
%%bigquery
create or replace table air_travel_int.Airport_Review as
    select distinct r.id, r.review_thread, r.review_date, r.review_author,
      r.review_subject, r.review_details, a.icao as airport_icao, r.broad_category, r.sub_category, r.sentiment,
      r.language, r._data_source, r._load_time
    from air_travel_stg.airport_reviews r join air_travel_int.Airport a
    on a.icao = r.airport_code

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Check uniqueness of primary key field

In [ ]:
%%bigquery
select id, count(*)
from air_travel_int.Airport_Review
group by id
having count(*) > 1

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [id, f0_]
Index: []

##### Check for foreign key violations

In [ ]:
%%bigquery
select count(*)
from air_travel_int.Airport_Review
where airport_icao not in (select icao from air_travel_int.Airport)

Query is running:   0%|          |

Downloading:   0%|          |

f0_
0    0

#### Create the Airport_Concessions, Airport_Establishment, and Food_Beverage tables (resolving anomaly types 8, 9, and 10)

In [ ]:
%%bigquery
select * from air_travel_stg.airport_maps
limit 10

Query is running:   0%|          |

Downloading:   0%|          |

airport             terminal                              business category  \
0     las           Terminal 1                                 Jamba   Dining   
1     aus        Baggage Claim                       Farmer's Fridge   Dining   
2     aus        Baggage Claim                High Brew Coffee Kiosk   Dining   
3     fll           Terminal 2                             Starbucks   Dining   
4     fll           Terminal 4                      Fresh Selections   Dining   
5     fll           Terminal 1       The Great American Bagel Bakery   Dining   
6     fll           Terminal 1                      Corona Beach Bar   Dining   
7     fll           Terminal 1                             Starbucks   Dining   
8     sba  Terminal 1, Level 2  Costa Terraza Restaurant & Tapas Bar   Dining   
9     cak           Terminal 1           Great Lakes Brewing Company   Dining   

                    location  dining  \
0              B/C Connector    True   
1              Baggage Claim    True   
2              Baggage Claim    True   
3        Baggage Claim Level    True   
4        Baggage Claim Level    True   
5        Baggage Claim Level    True   
6        Baggage Claim Level    True   
7        Baggage Claim Level    True   
8  Between Gate 2 and Gate 3    True   
9  Between Gate 3 and Gate 4    True   

                                          menu_items   _data_source  \
0                                          Smoothies  airport.guide   
1  Fresh salads, bowls, and snacks from a vending...  airport.guide   
2                            Canned cold brew coffee  airport.guide   
3                  Coffee, Tea, Pastries, Sandwiches  airport.guide   
4             Grab-and-Go Sandwiches, Salads, Snacks  airport.guide   
5           Bagels, Cream Cheese, Sandwiches, Coffee  airport.guide   
6                          Beer, Cocktails, Bar food  airport.guide   
7                  Coffee, Tea, Pastries, Sandwiches  airport.guide   
8             Tapas, cocktails, full restaurant menu  airport.guide   
9                            Craft beer and pub food  airport.guide   

                        _load_time  
0 2025-09-12 22:27:13.846732+00:00  
1 2025-09-12 22:27:13.846732+00:00  
2 2025-09-12 22:27:13.846732+00:00  
3 2025-09-12 22:27:13.846732+00:00  
4 2025-09-12 22:27:13.846732+00:00  
5 2025-09-12 22:27:13.846732+00:00  
6 2025-09-12 22:27:13.846732+00:00  
7 2025-09-12 22:27:13.846732+00:00  
8 2025-09-12 22:27:13.846732+00:00  
9 2025-09-12 22:27:13.846732+00:00

##### Create the Airport_Concessions junction table (resolving anomaly type 9)

In [ ]:
%%bigquery
select distinct a.icao as airport_icao, m.terminal, m.business, m.location, m._data_source, m._load_time
from air_travel_stg.airport_maps m join air_travel_int.Airport a
on upper(m.airport) = a.iata
where a.country = 'United States'
order by m.business

Query is running:   0%|          |

Downloading:   0%|          |

airport_icao            terminal                    business  \
0            KPSP  Terminal 1 Level 1    12th Fairway Bar & Grill   
1            KBOI        Second Floor   13th Street Pub and Grill   
2            KAUS      East Concourse                    24 Diner   
3            KAUS       Baggage Claim       24-Hour Flowers Kiosk   
4            KPIE                  T1  3 Daughters Brewing at PIE   
...           ...                 ...                         ...   
1401         KSFO          Terminal 1                      iStore   
1402         KHOU          Terminal 1                      iStore   
1403         KBDL       Main Terminal                      iStore   
1404         KLAX       International             iStore Boutique   
1405         KHDN          Terminal 1                     jetBlue   

                                           location   _data_source  \
0                       Post-security, near Gate 12  airport.guide   
1     Pre-security, near the TSA Security entrance.  airport.guide   
2                                      Near Gate 12  airport.guide   
3                                     Baggage Claim  airport.guide   
4                       First Floor, near Gates 2-6  airport.guide   
...                                             ...            ...   
1401          Harvey Milk Terminal 1, Post-Security  airport.guide   
1402                   West Concourse, near Gate 28  airport.guide   
1403                    Central area, post-security  airport.guide   
1404                                     Great Hall  airport.guide   
1405               Near ATM (12) and Play Area (14)  airport.guide   

                           _load_time  
0    2025-09-12 22:27:13.846732+00:00  
1    2025-09-12 22:27:13.846732+00:00  
2    2025-09-12 22:27:13.846732+00:00  
3    2025-09-12 22:27:13.846732+00:00  
4    2025-09-12 22:27:13.846732+00:00  
...                               ...  
1401 2025-09-12 22:27:13.846732+00:00  
1402 2025-09-12 22:27:13.846732+00:00  
1403 2025-09-12 22:27:13.846732+00:00  
1404 2025-09-12 22:27:13.846732+00:00  
1405 2025-09-12 22:27:13.846732+00:00  

[1406 rows x 6 columns]

In [ ]:
%%bigquery
create or replace table air_travel_int.Airport_Concessions as
  select distinct a.icao as airport_icao, m.terminal, m.business, m.location, m._data_source, m._load_time
  from air_travel_stg.airport_maps m join air_travel_int.Airport a
  on upper(m.airport) = a.iata
  where a.country = 'United States'
  order by m.business

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
select * from air_travel_int.Airport_Concessions
limit 10

Query is running:   0%|          |

Downloading:   0%|          |

airport_icao            terminal                    business  \
0         KPSP  Terminal 1 Level 1    12th Fairway Bar & Grill   
1         KBOI        Second Floor   13th Street Pub and Grill   
2         KAUS      East Concourse                    24 Diner   
3         KAUS       Baggage Claim       24-Hour Flowers Kiosk   
4         KPIE                  T1  3 Daughters Brewing at PIE   
5         KLAS          Terminal 1        360 Gourmet Burritos   
6         KSFO          Terminal 2              49 Mile Market   
7         KLGB          Terminal 1                    4th Vine   
8         KLGB          Terminal 1              562 Experience   
9         KFLL          Terminal 1                5th & Sunset   

                                        location   _data_source  \
0                    Post-security, near Gate 12  airport.guide   
1  Pre-security, near the TSA Security entrance.  airport.guide   
2                                   Near Gate 12  airport.guide   
3                                  Baggage Claim  airport.guide   
4                    First Floor, near Gates 2-6  airport.guide   
5                          Gate B, near Gate B15  airport.guide   
6                                    Concourse C  airport.guide   
7               Central Promenade, post-security  airport.guide   
8                  North Concourse, near Gate G1  airport.guide   
9                  Departure Level, near Gate A2  airport.guide   

                        _load_time  
0 2025-09-12 22:27:13.846732+00:00  
1 2025-09-12 22:27:13.846732+00:00  
2 2025-09-12 22:27:13.846732+00:00  
3 2025-09-12 22:27:13.846732+00:00  
4 2025-09-12 22:27:13.846732+00:00  
5 2025-09-12 22:27:13.846732+00:00  
6 2025-09-12 22:27:13.846732+00:00  
7 2025-09-12 22:27:13.846732+00:00  
8 2025-09-12 22:27:13.846732+00:00  
9 2025-09-12 22:27:13.846732+00:00

##### Check uniqueness of primary key fields (airport_icao, terminal, business, location)

In [ ]:
%%bigquery
select airport_icao, terminal, business, location, count(*) as count
from air_travel_int.Airport_Concessions
group by airport_icao, terminal, business, location
having count(*) > 1

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [airport_icao, terminal, business, location, count]
Index: []

##### Create the Airport_Establishment table

In [ ]:
%%bigquery
select distinct business, category, dining, _data_source, _load_time
from air_travel_stg.airport_maps
order by category, business

Query is running:   0%|          |

Downloading:   0%|          |

business         category  dining   _data_source  \
0      Kamaka Air Freight      Air Freight   False  airport.guide   
1     Air Canada Airlines          Airline   False  airport.guide   
2               Air Train          Airline   False  airport.guide   
3                  Alaska          Airline   False  airport.guide   
4          Alaska Airline          Airline   False  airport.guide   
...                   ...              ...     ...            ...   
1063      Vending Machine  Vending Machine   False  airport.guide   
1064      Vending Machine  Vending Machine    True  airport.guide   
1065     Vending Machines  Vending Machine    True  airport.guide   
1066      Vending Service  Vending Machine    True  airport.guide   
1067            Vino Volo         Wine Bar    True  airport.guide   

                           _load_time  
0    2025-09-12 22:27:13.846732+00:00  
1    2025-09-12 22:27:13.846732+00:00  
2    2025-09-12 22:27:13.846732+00:00  
3    2025-09-12 22:27:13.846732+00:00  
4    2025-09-12 22:27:13.846732+00:00  
...                               ...  
1063 2025-09-12 22:27:13.846732+00:00  
1064 2025-09-12 22:27:13.846732+00:00  
1065 2025-09-12 22:27:13.846732+00:00  
1066 2025-09-12 22:27:13.846732+00:00  
1067 2025-09-12 22:27:13.846732+00:00  

[1068 rows x 5 columns]

In [ ]:
%%bigquery
create or replace table air_travel_int.Airport_Establishment as
  select distinct business, category, dining, _data_source, _load_time
  from air_travel_stg.airport_maps
  order by category, business

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Check the uniqueness of primary key field

In [ ]:
%%bigquery
select distinct business, count(*)
from air_travel_int.Airport_Establishment
group by business
having count(*) > 1

Query is running:   0%|          |

Downloading:   0%|          |

business  f0_
0                Alaska Airlines    3
1                      Allegiant    2
2             Allegiant Airlines    3
3              American Airlines    5
4                 Breeze Airways    2
5                Delta Air Lines    4
6                 Delta Airlines    5
7              Frontier Airlines    3
8             Southwest Airlines    4
9                Spirit Airlines    3
10                        United    3
11               United Airlines    3
12  Delta Baggage Service Office    2
13                   Delta Cargo    2
14                    Air Canada    2
15                Delta Sky Club    3
16                 Escape Lounge    3
17                   United Club    3
18                           ATM    4
19               Business Center    2
20             Conference Center    2
21               Conference Room    2
22                        Inform    2
23                   Information    2
24                 Parking Kiosk    2
25                           USO    2
26               Business Lounge    2
27           Car Rental National    2
28             Currency Exchange    2
29                    Rental Car    4
30                    Shoe Shine    2
31                 Peet's Coffee    2
32                     Starbucks    2
33                   Burger King    2
34      California Pizza Kitchen    2
35            GTR Cafe and Gifts    2
36                   Hudson News    2
37                   Jamba Juice    2
38                        Subway    2
39               Vending Machine    4
40              Vending Machines    2
41                     Vino Volo    2
42         Brighton Collectibles    2
43                    Brookstone    2
44                          CNBC    2
45                      InMotion    2
46                 Lottery Kiosk    2
47                 MAC Cosmetics    2
48                 See's Candies    2
49               World Duty Free    2
50                        iStore    2

In [ ]:
%%bigquery
select *
from air_travel_int.Airport_Establishment
where business in (
    select business
    from air_travel_int.Airport_Establishment
    group by business
    having count(*) > 1
)
order by business

Query is running:   0%|          |

Downloading:   0%|          |

business           category  dining   _data_source  \
0                ATM  Financial Service   False  airport.guide   
1                ATM           Services   False  airport.guide   
2                ATM   Airport Services   False  airport.guide   
3                ATM    Airport Service   False  airport.guide   
4         Air Canada  Airline Ticketing   False  airport.guide   
..               ...                ...     ...            ...   
122        Vino Volo           Wine Bar    True  airport.guide   
123  World Duty Free             Retail   False  airport.guide   
124  World Duty Free           Shopping   False  airport.guide   
125           iStore             Retail   False  airport.guide   
126           iStore           Shopping   False  airport.guide   

                          _load_time  
0   2025-09-12 22:27:13.846732+00:00  
1   2025-09-12 22:27:13.846732+00:00  
2   2025-09-12 22:27:13.846732+00:00  
3   2025-09-12 22:27:13.846732+00:00  
4   2025-09-12 22:27:13.846732+00:00  
..                               ...  
122 2025-09-12 22:27:13.846732+00:00  
123 2025-09-12 22:27:13.846732+00:00  
124 2025-09-12 22:27:13.846732+00:00  
125 2025-09-12 22:27:13.846732+00:00  
126 2025-09-12 22:27:13.846732+00:00  

[127 rows x 5 columns]

In [ ]:
%%bigquery
select *
from air_travel_int.Airport_Establishment
where business = 'Starbucks'

Query is running:   0%|          |

Downloading:   0%|          |

business     category  dining   _data_source  \
0  Starbucks  Coffee Shop    True  airport.guide   
1  Starbucks       Dining    True  airport.guide   

                        _load_time  
0 2025-09-12 22:27:13.846732+00:00  
1 2025-09-12 22:27:13.846732+00:00

##### Map the `category` to a canonical category and remove the duplicate entries with `SELECT DISTINCT`

In [ ]:
%%bigquery
create or replace table air_travel_tmp.airport_establishment_raw_categories as
  select distinct business, category
  from air_travel_int.Airport_Establishment
  where category not in ('Airline', 'Airline Service', 'Airline Services', 'Airline Check-in', 'Airline Ticketing',
      'Airline Gate / Check-in', 'Airline Lounge', 'Airport Lounge', 'Airport Service', 'Airport Services', 'Air Freight', 'Car Rental',
      'Information Kiosk', 'Information Service', 'Parking', 'Transportation Service')

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
select * from air_travel_tmp.airport_establishment_raw_categories
order by business
limit 10

Query is running:   0%|          |

Downloading:   0%|          |

business  category
0    12th Fairway Bar & Grill    Dining
1   13th Street Pub and Grill    Dining
2                    24 Diner    Dining
3       24-Hour Flowers Kiosk  Shopping
4  3 Daughters Brewing at PIE    Dining
5        360 Gourmet Burritos    Dining
6              49 Mile Market  Shopping
7                    4th Vine    Dining
8              562 Experience  Shopping
9                5th & Sunset  Shopping

##### Prepare the canonical categories

In [ ]:
%%bigquery
create or replace table air_travel_tmp.airport_establishment_canonical_categories (
     broad_category string,
     sub_category string
)

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
insert into air_travel_tmp.airport_establishment_canonical_categories (broad_category, sub_category)
values
  ('Quick Service & Grab-and-Go', 'National/International Fast Food Chains'),
  ('Quick Service & Grab-and-Go', 'Coffee & Beverage Shops'),
  ('Quick Service & Grab-and-Go', 'Snack Kiosks'),
  ('Quick Service & Grab-and-Go', 'Pre-Packaged Foods'),
  ('Fast Casual', 'Gourmet Burgers & Sandwiches'),
  ('Fast Casual', 'Build-Your-Own Concepts'),
  ('Fast Casual', 'Pizzerias'),
  ('Full-Service Dining', 'Casual Dining Restaurants'),
  ('Full-Service Dining', 'Upscale & Chef-Driven Restaurants'),
  ('Full-Service Dining', 'Themed Restaurants & Sports Bars'),
  ('Bars & Lounges', 'Wine Bars'),
  ('Bars & Lounges', 'Craft Beer Pubs'),
  ('Bars & Lounges', 'Cocktail Lounges'),
  ('Travel Essentials & Convenience', 'Newsstands & Bookstores'),
  ('Travel Essentials & Convenience', 'Pharmacies & Personal Care'),
  ('Travel Essentials & Convenience', 'Travel Gear & Luggage'),
  ('Specialty Retail', 'Electronics'),
  ('Specialty Retail', 'Local Souvenirs & Gifts'),
  ('Specialty Retail', 'Apparel & Accessories'),
  ('Luxury & High-End Goods', 'Confectionery & Gourmet Foods'),
  ('Luxury & High-End Goods', 'Designer Fashion'),
  ('Luxury & High-End Goods', 'Jewelry & Watches'),
  ('Luxury & High-End Goods', 'High-End Cosmetics'),
  ('Duty-Free', 'Liquor & Tobacco'),
  ('Duty-Free', 'Fragrances & Cosmetics'),
  ('Duty-Free', 'Luxury Accessories & Confectionery'),
  ('Passenger Comfort & Wellness', 'Spas & Salons'),
  ('Passenger Comfort & Wellness', 'Pay-Per-Use Lounges'),
  ('Passenger Comfort & Wellness', 'Yoga & Meditation Rooms'),
  ('Passenger Comfort & Wellness', 'Shower Facilities'),
  ('Financial & Business Services', 'Currency Exchange'),
  ('Financial & Business Services', 'ATMs & Banking Services'),
  ('Financial & Business Services', 'Business Centers & Work Pods'),
  ('Practical & Convenience Services', 'Luggage Storage & Wrapping'),
  ('Practical & Convenience Services', 'Postal & Shipping Services'),
  ('Practical & Convenience Services', 'Pet Relief & Care Areas'),
  ('Practical & Convenience Services', 'Vending Machines (non-F&B)')

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
select * from air_travel_tmp.airport_establishment_canonical_categories
limit 10

Query is running:   0%|          |

Downloading:   0%|          |

broad_category                        sub_category
0                 Bars & Lounges                           Wine Bars
1                 Bars & Lounges                     Craft Beer Pubs
2                 Bars & Lounges                    Cocktail Lounges
3                      Duty-Free                    Liquor & Tobacco
4                      Duty-Free  Luxury Accessories & Confectionery
5                      Duty-Free              Fragrances & Cosmetics
6                    Fast Casual        Gourmet Burgers & Sandwiches
7                    Fast Casual                           Pizzerias
8                    Fast Casual             Build-Your-Own Concepts
9  Financial & Business Services        Business Centers & Work Pods

In [ ]:
%%bigquery
create or replace table air_travel_tmp.airport_establishment_mapped_broad_categories as
  with canonical_categories as (
    select ARRAY_AGG(distinct broad_category) AS broad_categories
    from air_travel_tmp.airport_establishment_canonical_categories
  ),
  airport_establishment_tmp as (
    select
      business,
      category as raw_category,
      AI.GENERATE(
        ('Map the business ', business, ' to its most fitting broad category from this canonical category list:',
          broad_categories),
        connection_id => 'us-central1.vertex-ai-connection',
        endpoint => 'gemini-2.5-flash-lite',
        model_params => JSON '{"generation_config":{"thinking_config": {"thinking_budget": 0}}, "tools": [{"googleSearch": {}}]}',
        output_schema => 'broad_category STRING') as llm_response
    from air_travel_tmp.airport_establishment_raw_categories
    cross join canonical_categories
  )
select business, raw_category, llm_response.broad_category as broad_category
from airport_establishment_tmp

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
select * from air_travel_tmp.airport_establishment_mapped_broad_categories

Query is running:   0%|          |

Downloading:   0%|          |

business          raw_category  \
0        Pyramid Ale Taproom  Restaurant / Brewery   
1                    Bar 510                   Bar   
2              Gaming Lounge         Entertainment   
3               Tap and Pour      Bar / Restaurant   
4                      8 Bar                   Bar   
..                       ...                   ...   
848               MillsCargo              Shopping   
849          Good Time Clock          Things to Do   
850                   Fiesta          Things to Do   
851  TV Room Business Center          Things to Do   
852            SB Sky Gazing          Things to Do   

                       broad_category  
0                      Bars & Lounges  
1                      Bars & Lounges  
2                      Bars & Lounges  
3                      Bars & Lounges  
4                      Bars & Lounges  
..                                ...  
848   Travel Essentials & Convenience  
849                    Bars & Lounges  
850                    Bars & Lounges  
851  Practical & Convenience Services  
852                  Specialty Retail  

[853 rows x 3 columns]

In [ ]:
%%bigquery
create or replace table air_travel_tmp.airport_establishment_mapped_sub_categories as
  with tmp_establishment_categories as (
    select m.business, m.broad_category,
      array_agg(distinct c.sub_category) AS sub_categories
    from air_travel_tmp.airport_establishment_mapped_broad_categories m
    join air_travel_tmp.airport_establishment_canonical_categories c
    on m.broad_category = c.broad_category
    where m.broad_category is not null
    group by m.business, m.broad_category
  ),
  airport_establishment_tmp as (
    select
      business,
      broad_category,
      AI.GENERATE(
        ('Map the airport concession ', business, ' with broad category ', broad_category,
        ' to its most fitting sub category based on this canonical list of subcategories: ', sub_categories),
        connection_id => 'us-central1.vertex-ai-connection',
        endpoint => 'gemini-2.5-flash-lite',
        model_params => JSON '{"generation_config":{"thinking_config": {"thinking_budget": 0}}, "tools": [{"googleSearch": {}}]}',
        output_schema => 'sub_category STRING') as llm_response
    from tmp_establishment_categories
  )
select business, broad_category, llm_response.sub_category as sub_category
from airport_establishment_tmp

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
select * from air_travel_tmp.airport_establishment_mapped_sub_categories
limit 10

Query is running:   0%|          |

Downloading:   0%|          |

business  broad_category      sub_category
0              Susquehanna Club  Bars & Lounges  Cocktail Lounges
1                  Space Corner  Bars & Lounges  Cocktail Lounges
2                     I Love LA  Bars & Lounges  Cocktail Lounges
3              The Iron Compass  Bars & Lounges  Cocktail Lounges
4  Andalé Mexican Kitchen + Bar  Bars & Lounges  Cocktail Lounges
5       Scoreboard Bar and Café  Bars & Lounges  Cocktail Lounges
6                   Food/Lounge  Bars & Lounges  Cocktail Lounges
7           Syrenity bar market  Bars & Lounges  Cocktail Lounges
8                Mothers Lounge  Bars & Lounges  Cocktail Lounges
9           Seaside Stack Shack  Bars & Lounges  Cocktail Lounges

##### Re-create the final table with the new categories

In [ ]:
%%bigquery
create or replace table air_travel_int.Airport_Establishment as
  select distinct e.business, m.broad_category, m.sub_category,
    case when m.broad_category in ('Fast Casual', 'Full-Service Dining') then True else False end as dining,
    'airport.guide,llm' as _data_source, e._load_time
  from air_travel_int.Airport_Establishment e join air_travel_tmp.airport_establishment_mapped_sub_categories m
  on e.business = m.business

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
select * from air_travel_int.Airport_Establishment
limit 10

Query is running:   0%|          |

Downloading:   0%|          |

business  broad_category      sub_category  dining  \
0                  La Familia  Bars & Lounges  Cocktail Lounges   False   
1                   Java Moon  Bars & Lounges  Cocktail Lounges   False   
2                   Aviator's  Bars & Lounges  Cocktail Lounges   False   
3      Jose Cuervo Tequileria  Bars & Lounges  Cocktail Lounges   False   
4                    Haymaker  Bars & Lounges  Cocktail Lounges   False   
5            Corona Beach Bar  Bars & Lounges  Cocktail Lounges   False   
6              Chart Room Bar  Bars & Lounges  Cocktail Lounges   False   
7                 Zocalo Cafe  Bars & Lounges  Cocktail Lounges   False   
8  Nacho Hippo Cantina Maximo  Bars & Lounges  Cocktail Lounges   False   
9                  Poker Face  Bars & Lounges  Cocktail Lounges   False   

        _data_source                       _load_time  
0  airport.guide,llm 2025-09-12 22:27:13.846732+00:00  
1  airport.guide,llm 2025-09-12 22:27:13.846732+00:00  
2  airport.guide,llm 2025-09-12 22:27:13.846732+00:00  
3  airport.guide,llm 2025-09-12 22:27:13.846732+00:00  
4  airport.guide,llm 2025-09-12 22:27:13.846732+00:00  
5  airport.guide,llm 2025-09-12 22:27:13.846732+00:00  
6  airport.guide,llm 2025-09-12 22:27:13.846732+00:00  
7  airport.guide,llm 2025-09-12 22:27:13.846732+00:00  
8  airport.guide,llm 2025-09-12 22:27:13.846732+00:00  
9  airport.guide,llm 2025-09-12 22:27:13.846732+00:00

##### Check uniqueness of the primary key field

In [ ]:
%%bigquery
select business, count(*)
from air_travel_int.Airport_Establishment
group by business
having count(*) > 1

Query is running:   0%|          |

Downloading:   0%|          |

business  f0_
0  InMotion    2

In [ ]:
%%bigquery
select *
from air_travel_int.Airport_Establishment
where business = 'InMotion'

Query is running:   0%|          |

Downloading:   0%|          |

business                    broad_category                sub_category  \
0  InMotion      Passenger Comfort & Wellness         Pay-Per-Use Lounges   
1  InMotion  Practical & Convenience Services  Vending Machines (non-F&B)   

   dining       _data_source                       _load_time  
0   False  airport.guide,llm 2025-09-12 22:27:13.846732+00:00  
1   False  airport.guide,llm 2025-09-12 22:27:13.846732+00:00

In [ ]:
%%bigquery
delete from air_travel_int.Airport_Establishment
where business = 'InMotion' and broad_category = 'Passenger Comfort & Wellness'

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Create the Food_Beverage table

In [ ]:
%%bigquery
select e.business, split(m.menu_items, ',') as menu_items
from air_travel_int.Airport_Establishment e join air_travel_stg.airport_maps m
on e.business = m.business
where e.dining = True
order by business

Query is running:   0%|          |

Downloading:   0%|          |

business                                         menu_items
0                 24 Diner        [American diner food,  breakfast,  burgers]
1             5th & Sunset                                                 []
2                   Alfred                      [Specialty coffee,  pastries]
3           American Grill  [Classic American food,  burgers,  sandwiches,...
4              Amoura Cafe                           [Mediterranean classics]
..                     ...                                                ...
152     Urth Caffe and Bar  [Organic coffee,  tea,  pastries,  salads,  sa...
153  Villa Italian Kitchen                                     [Italian food]
154      Wahoo's Fish Taco                    [Fish tacos,  burritos,  bowls]
155                 Wakaba                                [Sushi,  bento box]
156         Yia Yia Mary's                    [Greek,  Mediterranean Cuisine]

[157 rows x 2 columns]

##### Flatten the menu_items field

In [ ]:
%%bigquery
select business, menu_item
from
  (select e.business, split(m.menu_items, ',') as menu_items
   from air_travel_int.Airport_Establishment e join air_travel_stg.airport_maps m
    on e.business = m.business
    where e.dining = True) t, unnest(t.menu_items) as menu_item
order by business

Query is running:   0%|          |

Downloading:   0%|          |

business               menu_item
0             24 Diner     American diner food
1             24 Diner               breakfast
2             24 Diner                 burgers
3         5th & Sunset                        
4               Alfred        Specialty coffee
..                 ...                     ...
351  Wahoo's Fish Taco                   bowls
352             Wakaba                   Sushi
353             Wakaba               bento box
354     Yia Yia Mary's                   Greek
355     Yia Yia Mary's   Mediterranean Cuisine

[356 rows x 2 columns]

##### Create the final table (resolving anomaly type 8)

In [ ]:
%%bigquery
create or replace table air_travel_int.Food_Beverage as
  select distinct business, menu_item
  from
    (select e.business, split(m.menu_items, ',') as menu_items
    from air_travel_int.Airport_Establishment e join air_travel_stg.airport_maps m
    on e.business = m.business
    where e.dining = True) t, unnest(t.menu_items) as menu_item
  order by business

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
select * from air_travel_int.Food_Beverage
limit 10

Query is running:   0%|          |

Downloading:   0%|          |

business              menu_item
0        24 Diner    American diner food
1        24 Diner              breakfast
2        24 Diner                burgers
3    5th & Sunset                       
4          Alfred       Specialty coffee
5          Alfred               pastries
6  American Grill  Classic American food
7  American Grill                burgers
8  American Grill             sandwiches
9  American Grill        breakfast items

##### Check for uniqueness of primary key fields (`business`, `menu_item`)

In [ ]:
%%bigquery
select business, menu_item, count(*) as count
from air_travel_int.Food_Beverage
group by business, menu_item
having count(*) > 1

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [business, menu_item, count]
Index: []

##### Check foreign key constraint on `business`

In [ ]:
%%bigquery
select count(*)
from air_travel_int.Food_Beverage
where business not in
  (select business from air_travel_int.Airport_Establishment)

Query is running:   0%|          |

Downloading:   0%|          |

f0_
0    0

##### Also, check foreign key constraint on Airport_Concessions

In [ ]:
%%bigquery
select count(*)
from air_travel_int.Airport_Concessions
where business not in
  (select business from air_travel_int.Airport_Establishment)

Query is running:   0%|          |

Downloading:   0%|          |

f0_
0  263

In [ ]:
%%bigquery
select *
from air_travel_int.Airport_Concessions
where business not in
  (select business from air_travel_int.Airport_Establishment)
limit 10

Query is running:   0%|          |

Downloading:   0%|          |

airport_icao                                           terminal  \
0         KBLI                                         Terminal 1   
1         KAVL                                Terminal 1, Level 1   
2         KCMH                                          Ticketing   
3         KCVG  Cincinnati - Northern Kentucky International A...   
4         KEGE                                 Terminal 1 Level 1   
5         KBMI                                      Main Terminal   
6         KLIT                                         Terminal 2   
7         KMYR                                         Terminal 1   
8         KBUF                                 Terminal 1 Level 2   
9         KLEX                                            Level 1   

                    business  \
0           ALASKA AIR CARGO   
1                    ATM USA   
2                 Air Canada   
3                 Air Canada   
4        Air Canada Airlines   
5                  Air Train   
6     Airline Baggage Office   
7        Airport Information   
8  Airport Lounge “The Club”   
9           Airport Services   

                                            location   _data_source  \
0                Near the baggage hall and main exit  airport.guide   
1                   Post-security, central concourse  airport.guide   
2  Ticketing counter, between United Airlines and...  airport.guide   
3  Ticketing, near Viva Aerobus and American Airl...  airport.guide   
4                                       Ticket Lobby  airport.guide   
5                   Level 1, Airline Ticket Counters  airport.guide   
6            Near the Nursing Room and Baggage Claim  airport.guide   
7                              Level 1, pre-security  airport.guide   
8                                        Near Gate 6  airport.guide   
9  Post-security, in the central area between the...  airport.guide   

                        _load_time  
0 2025-09-12 22:27:13.846732+00:00  
1 2025-09-12 22:27:13.846732+00:00  
2 2025-09-12 22:27:13.846732+00:00  
3 2025-09-12 22:27:13.846732+00:00  
4 2025-09-12 22:27:13.846732+00:00  
5 2025-09-12 22:27:13.846732+00:00  
6 2025-09-12 22:27:13.846732+00:00  
7 2025-09-12 22:27:13.846732+00:00  
8 2025-09-12 22:27:13.846732+00:00  
9 2025-09-12 22:27:13.846732+00:00

Delete the orphan records from the Airport_Concessions table (we don't want them in the table because they don't represent concessions)

In [ ]:
%%bigquery
delete from air_travel_int.Airport_Concessions
where business not in
  (select business from air_travel_int.Airport_Establishment)

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
select *
from air_travel_int.Airport_Concessions
limit 10

Query is running:   0%|          |

Downloading:   0%|          |

airport_icao                    terminal                 business  \
0          HTS          Terminal 1 Level 1  Giovanni's - On the Fly   
1         KABQ  Third Level A/B Concourses               Food Court   
2         KABQ    Third Level Pre-Security        Black Mesa Coffee   
3         KABQ                 First Floor         Vending Machines   
4         KABQ  Third Level A/B Concourses               Misc Shops   
5         KABQ  Third Level A/B Concourses   Rio Grande Pub & Grill   
6         KABQ  Third Level A/B Concourses        Black Mesa Coffee   
7         KABQ  Third Level A/B Concourses               Keva Juice   
8         KABQ  Third Level A/B Concourses             Schlotzsky's   
9         KABQ  Third Level A/B Concourses              Hudson News   

                                            location   _data_source  \
0  Near the TSA Office and Security Screening Ent...  airport.guide   
1           Between concourses A and B, near Gate B1  airport.guide   
2  Near Aviation Admin Offices, before TSA Checkp...  airport.guide   
3  Near Delta, American, Alaska, JetBlue, United ...  airport.guide   
4        Near Food Court, between concourses A and B  airport.guide   
5                                       Near Gate A1  airport.guide   
6                                      Near Gate A12  airport.guide   
7                                       Near Gate A3  airport.guide   
8                                       Near Gate A5  airport.guide   
9                                       Near Gate A5  airport.guide   

                        _load_time  
0 2025-09-12 22:27:13.846732+00:00  
1 2025-09-12 22:27:13.846732+00:00  
2 2025-09-12 22:27:13.846732+00:00  
3 2025-09-12 22:27:13.846732+00:00  
4 2025-09-12 22:27:13.846732+00:00  
5 2025-09-12 22:27:13.846732+00:00  
6 2025-09-12 22:27:13.846732+00:00  
7 2025-09-12 22:27:13.846732+00:00  
8 2025-09-12 22:27:13.846732+00:00  
9 2025-09-12 22:27:13.846732+00:00

#### Create the Airline table

In [ ]:
%%bigquery
select * from air_travel_stg.airlines
limit 10

Query is running:   0%|          |

Downloading:   0%|          |

id                            name alias  iata  icao       callsign  \
0  3562                     Multiflight  None  None   MFT        YORKAIR   
1  5556                            buzz  None    UK   BUZ           None   
2  2636  Gulf African Airlines - Gambia  None  None   GUF   GULF AFRICAN   
3  4854                           Sirin  None    R1  None           None   
4  4430                Scorpio Aviation  None    8S  None           None   
5  2080         Electronic Data Systems  None  None    1Y           None   
6  1509               Bellview Airlines  None  None   BVU   Sierra Leone   
7  2804                            ICAO  None  None   YYY           None   
8  2649             Guyana Airways 2000  None    GY  None           None   
9  1516                      BAX Global  None    8W  None           None   

  country active _data_source                       _load_time  
0    None      N  openflights 2025-09-05 17:02:52.385895+00:00  
1    None      N  openflights 2025-09-05 17:02:52.385895+00:00  
2    None      N  openflights 2025-09-05 17:02:52.385895+00:00  
3    None      N  openflights 2025-09-05 17:02:52.385895+00:00  
4    None      N  openflights 2025-09-05 17:02:52.385895+00:00  
5    None      N  openflights 2025-09-05 17:02:52.385895+00:00  
6    None      N  openflights 2025-09-05 17:02:52.385895+00:00  
7    None      N  openflights 2025-09-05 17:02:52.385895+00:00  
8    None      N  openflights 2025-09-05 17:02:52.385895+00:00  
9    None      N  openflights 2025-09-05 17:02:52.385895+00:00

##### Look for any unmatched countries (as country_code will be a foreign key on this table)

In [ ]:
%%bigquery
select distinct name as airline, country
from air_travel_stg.airlines
where country not in (select name from air_travel_int.Country)
order by country

Query is running:   0%|          |

Downloading:   0%|          |

airline                country
0                    Sedalia   Boonville Stage Line
1                      Aires                   S.A.
2    Southern Jersey Airways                   ACOM
3        Active Aero Charter            ACTIVE AERO
4                 Aerocenter             AEROCENTER
..                       ...                    ...
210     Syrian Arab Airlines   Syrian Arab Republic
211   Empresa (Aero Uruguay)          UNIFORM OSCAR
212             RAF St Athan         UNited Kingdom
213                    Veles                  VELES
214  Ministry of Agriculture               WATCHDOG

[215 rows x 2 columns]

##### Use the language model to look up the iso codes for the orphan countries

In [ ]:
%%bigquery
create or replace table air_travel_tmp.airline_mapped_countries as
  with airline_orphan_countries as (
    select distinct country
    from air_travel_stg.airlines
    where country not in (select name from air_travel_int.Country)
  ),
  airline_country as (
    select
      country,
      AI.GENERATE(
        ('If ', country, ' is a recognized country, return its iso code. If it is not a recognized country, return None.'),
        connection_id => 'us-central1.vertex-ai-connection',
        endpoint => 'gemini-2.5-flash-lite',
        model_params => JSON '{"generation_config":{"thinking_config": {"thinking_budget": 0}}, "tools": [{"googleSearch": {}}]}',
        output_schema => 'iso_code STRING') as llm_response
    from airline_orphan_countries
  )
  select country as original_country, llm_response.iso_code as mapped_iso_code
  from airline_country

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
select *
from air_travel_tmp.airline_mapped_countries

Query is running:   0%|          |

Downloading:   0%|          |

original_country mapped_iso_code
0                             Brunei              BN
1       Democratic Republic of Congo              CD
2                   Congo (Kinshasa)              CD
3   Democratic Republic of the Congo              CD
4                        Ivory Coast              CI
..                               ...             ...
82                Russian Federation              RU
83                   Somali Republic              SO
84              Syrian Arab Republic             SYR
85                         Swaziland              SZ
86  Saint Vincent and the Grenadines              VC

[87 rows x 2 columns]

##### Create the final table, reordering the fields and adding the  iso code from the Country table

In [ ]:
%%bigquery
create or replace table air_travel_int.Airline as
  select a.id, a.name, a.alias, a.icao, a.iata, a.callsign, a.country as country_name, c.iso_code as country_code, a.active, a._data_source, a._load_time
  from air_travel_stg.airlines a left join air_travel_int.Country c
  on a.country = c.name

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
select * from air_travel_int.Airline
limit 10

Query is running:   0%|          |

Downloading:   0%|          |

id                            name alias  icao  iata       callsign  \
0  4051                    Princess Air  None  None    8Q           None   
1  2649             Guyana Airways 2000  None  None    GY           None   
2  2636  Gulf African Airlines - Gambia  None   GUF  None   GULF AFRICAN   
3  1509               Bellview Airlines  None   BVU  None   Sierra Leone   
4  4430                Scorpio Aviation  None  None    8S           None   
5  3562                     Multiflight  None   MFT  None        YORKAIR   
6  4854                           Sirin  None  None    R1           None   
7  2080         Electronic Data Systems  None    1Y  None           None   
8  5199         Transports et Travaux A  None  None    OF           None   
9  5556                            buzz  None   BUZ    UK           None   

  country_name country_code active _data_source  \
0         None         None      N  openflights   
1         None         None      N  openflights   
2         None         None      N  openflights   
3         None         None      N  openflights   
4         None         None      N  openflights   
5         None         None      N  openflights   
6         None         None      N  openflights   
7         None         None      N  openflights   
8         None         None      N  openflights   
9         None         None      N  openflights   

                        _load_time  
0 2025-09-05 17:02:52.385895+00:00  
1 2025-09-05 17:02:52.385895+00:00  
2 2025-09-05 17:02:52.385895+00:00  
3 2025-09-05 17:02:52.385895+00:00  
4 2025-09-05 17:02:52.385895+00:00  
5 2025-09-05 17:02:52.385895+00:00  
6 2025-09-05 17:02:52.385895+00:00  
7 2025-09-05 17:02:52.385895+00:00  
8 2025-09-05 17:02:52.385895+00:00  
9 2025-09-05 17:02:52.385895+00:00

In [ ]:
%%bigquery
update air_travel_int.Airline a
  set country_code = (select mapped_iso_code from air_travel_tmp.airline_mapped_countries m
                      where a.country_name = m.original_country)
  where country_code is null
  and country_name is not null

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
create or replace table air_travel_int.Airline as
  select * except (country_name)
  from air_travel_int.Airline

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
select * from air_travel_int.Airline
limit 10

Query is running:   0%|          |

Downloading:   0%|          |

id                                 name alias icao  iata  \
0   446                Aerosun International  None  ASI  None   
1   554                Airways International  None  AWB  None   
2   865                  Argentine Air Force  None  FAG  None   
3  5029  TAPSA Transportes Aereos Petroleros  None  TPS  None   
4  3682                Nordstree (Australia)  None  NDS  None   
5  4331                          Sky Bahamas  None  SBM  None   
6  4873                          TNT Airways  None  TAY    3V   
7   301                   Air Minas Linhas A  None  AMG  None   
8  1095                            Air Sport  None  MSK  None   
9  1506        Bulgarian Aeronautical Centre  None  BVC  None   

          callsign country_code active _data_source  \
0             Inc.         None      N  openflights   
1             Inc.         None      N  openflights   
2            FUAER           AR      N  openflights   
3            TAPSA           AR      N  openflights   
4             None           AU      N  openflights   
5      SKY BAHAMAS           BS      N  openflights   
6          QUALITY           BE      N  openflights   
7        AIR MINAS           BR      N  openflights   
8        AIR SPORT           BG      N  openflights   
9  BULGARIAN WINGS           BG      N  openflights   

                        _load_time  
0 2025-09-05 17:02:52.385895+00:00  
1 2025-09-05 17:02:52.385895+00:00  
2 2025-09-05 17:02:52.385895+00:00  
3 2025-09-05 17:02:52.385895+00:00  
4 2025-09-05 17:02:52.385895+00:00  
5 2025-09-05 17:02:52.385895+00:00  
6 2025-09-05 17:02:52.385895+00:00  
7 2025-09-05 17:02:52.385895+00:00  
8 2025-09-05 17:02:52.385895+00:00  
9 2025-09-05 17:02:52.385895+00:00

In [ ]:
%%bigquery
select count(*) from air_travel_int.Airline

Query is running:   0%|          |

Downloading:   0%|          |

f0_
0  6162

##### Check primary key uniqueness

In [ ]:
%%bigquery
select id, count(*) as count
from air_travel_int.Airline
group by id
having count(*) > 1

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [id, count]
Index: []

##### Check for orphan countries, note that nulls are ok


In [ ]:
%%bigquery
select distinct country_code
from air_travel_int.Airline
where country_code not in (select iso_code from air_travel_int.Country)
and country_code is not null

Query is running:   0%|          |

Downloading:   0%|          |

country_code
0          KOR
1          FRO
2          COG
3          SYR
4          LAO

##### Use the language model to look up the attributes of these countries (country name and dafif_codes) and add them as new records to the Country table

In [ ]:
%%bigquery
create or replace table air_travel_tmp.airlines_countries_new as
  with airline_orphan_countries as (
    select distinct country_code
    from air_travel_int.Airline
    where country_code not in (select iso_code from air_travel_int.Country)
    and country_code is not null
  ),
  countries_new as (
    select
      country_code,
      AI.GENERATE(
        ('What are the country name and dafif_code that map to iso code', country_code, '? If you cannot find them, return None.'),
        connection_id => 'us-central1.vertex-ai-connection',
        endpoint => 'gemini-2.5-flash-lite',
        model_params => JSON '{"generation_config":{"thinking_config": {"thinking_budget": 0}}, "tools": [{"googleSearch": {}}]}',
        output_schema => 'country_name STRING, dafif_code STRING') as llm_response
    from airline_orphan_countries
  )
select country_code, llm_response.country_name as country_name, llm_response.dafif_code as dafif_code
from countries_new

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
select * from air_travel_tmp.airlines_countries_new

Query is running:   0%|          |

Downloading:   0%|          |

country_code           country_name dafif_code
0          LAO                   Laos         LS
1          KOR     Korea, Republic of         RK
2          SYR   Syrian Arab Republic         SY
3          COG  Republic of the Congo        CNG
4          FRO                 France         LF

In [ ]:
%%bigquery
insert into air_travel_int.Country (iso_code, name, dafif_codes, _data_source, _load_time)
  select country_code, country_name, array_agg(dafif_code), 'llm', current_timestamp()
  from air_travel_tmp.airlines_countries_new
  group by country_code, country_name

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
select * from air_travel_int.Country where iso_code in ('LAO', 'KOR', 'SYR', 'COG', 'FRO')

Query is running:   0%|          |

Downloading:   0%|          |

iso_code                   name dafif_codes _data_source  \
0      LAO                   Laos        [LS]          llm   
1      SYR   Syrian Arab Republic        [SY]          llm   
2      COG  Republic of the Congo       [CNG]          llm   
3      FRO                 France        [LF]          llm   
4      KOR     Korea, Republic of        [RK]          llm   

                        _load_time  
0 2025-10-12 21:58:51.011826+00:00  
1 2025-10-12 21:58:51.011826+00:00  
2 2025-10-12 21:58:51.011826+00:00  
3 2025-10-12 21:58:51.011826+00:00  
4 2025-10-12 21:58:51.011826+00:00

##### Recheck for orphan countries in the Airline table

In [ ]:
%%bigquery
select distinct country_code
from air_travel_int.Airline
where country_code not in (select iso_code from air_travel_int.Country)
and country_code is not null

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [country_code]
Index: []

#### Create the Aircraft table

In [ ]:
%%bigquery
select * from air_travel_stg.aircrafts
limit 10

Query is running:   0%|          |

Downloading:   0%|          |

name iata  icao _data_source                       _load_time
0   Boeing 757  757  None  openflights 2025-09-06 02:42:39.189193+00:00
1   Boeing 747  747  None  openflights 2025-09-06 02:42:39.189193+00:00
2      BAe 146  146  None  openflights 2025-09-06 02:42:39.189193+00:00
3   Boeing 767  767  None  openflights 2025-09-06 02:42:39.189193+00:00
4  Embraer 175  E75  None  openflights 2025-09-06 02:42:39.189193+00:00
5  Airbus A380  380  None  openflights 2025-09-06 02:42:39.189193+00:00
6   Boeing 737  737  None  openflights 2025-09-06 02:42:39.189193+00:00
7   Boeing 727  727  None  openflights 2025-09-06 02:42:39.189193+00:00
8  Airbus A340  340  None  openflights 2025-09-06 02:42:39.189193+00:00
9  Airbus A330  330  None  openflights 2025-09-06 02:42:39.189193+00:00

##### Aircraft types have unique icao codes too. Use the language model to look up the missing codes, so that we can use the icao as the primary key instead of the aircraft name

In [ ]:
%%bigquery
create or replace table air_travel_tmp.aircraft_icao as
  with aircrafts_tmp as (
    select
      name as aircraft_name,
      AI.GENERATE(
        ('What is the icao code of aircraft ', name, '? If it does not have one, return None.'),
        connection_id => 'us-central1.vertex-ai-connection',
        endpoint => 'gemini-2.5-flash-lite',
        model_params => JSON '{"generation_config":{"thinking_config": {"thinking_budget": 0}}, "tools": [{"googleSearch": {}}]}',
        output_schema => 'aircraft_icao STRING') as llm_response
    from air_travel_stg.aircrafts
    where icao is null
  )
select aircraft_name, llm_response.aircraft_icao
from aircrafts_tmp

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
select * from air_travel_tmp.aircraft_icao

Query is running:   0%|          |

Downloading:   0%|          |

aircraft_name aircraft_icao
0          Boeing 727          B727
1         Embraer 175          E175
2         Airbus A330          A330
3             BAe 146          BAE1
4          Boeing 747          B747
5          Boeing 787          B787
6   Boeing 737 MAX 10          BMAX
7          Boeing 737          B737
8          Boeing 767          B767
9         Airbus A380          A388
10        Airbus A340          A340
11         Boeing 777          B777
12        Airbus A350          A350
13         Boeing 757          B757

##### Create the final table with icao as the primary key

In [ ]:
%%bigquery
create or replace table air_travel_int.Aircraft as
    select icao, iata, name, _data_source, _load_time
    from air_travel_stg.aircrafts

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
update air_travel_int.Aircraft a
  set icao = (select aircraft_icao from air_travel_tmp.aircraft_icao i
              where a.name = i.aircraft_name)
  where icao is null

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
select * from air_travel_int.Aircraft
limit 10

Query is running:   0%|          |

Downloading:   0%|          |

icao  iata                        name _data_source  \
0  B727   727                  Boeing 727  openflights   
1  A20N   32N              Airbus A320neo  openflights   
2  E75L   E7W     Embraer 175 (long wing)  openflights   
3  B722   722              Boeing 727-200  openflights   
4  C56X   CNJ       Cessna Citation Excel  openflights   
5  LJ35   LRJ                  Learjet 35  openflights   
6  P28B  None  Piper PA-28 (above 200 hp)  openflights   
7  T154   TU5              Tupolev Tu-154  openflights   
8  A359   359             Airbus A350-900  openflights   
9  B77W   77W            Boeing 777-300ER  openflights   

                        _load_time  
0 2025-09-06 02:42:39.189193+00:00  
1 2025-09-06 02:42:39.189193+00:00  
2 2025-09-06 02:42:39.189193+00:00  
3 2025-09-06 02:42:39.189193+00:00  
4 2025-09-06 02:42:39.189193+00:00  
5 2025-09-06 02:42:39.189193+00:00  
6 2025-09-06 02:42:39.189193+00:00  
7 2025-09-06 02:42:39.189193+00:00  
8 2025-09-06 02:42:39.189193+00:00  
9 2025-09-06 02:42:39.189193+00:00

##### Recheck the primary key constraint

In [ ]:
%%bigquery
select count(*)
from air_travel_int.Aircraft
where icao is null

Query is running:   0%|          |

Downloading:   0%|          |

f0_
0    0

#### Create the Flight_Routes table (resolving anomaly type 9)

In [ ]:
%%bigquery
select * from air_travel_stg.flight_routes
limit 10

Query is running:   0%|          |

Downloading:   0%|          |

airline_code  airline_id source_airport  source_airport_id dest_airport  \
0           2B         410            DME               4029          TGK   
1           2G        1654            IKT               2937          KCK   
2           4O       17885            MEX               1824          PQM   
3           5Z       18946            CPT                797          PBZ   
4           6E        2850            BOM               2997          HYD   
5           6E        2850            BLR               3131          HYD   
6           6E        2850            CCU               3043          HYD   
7           6E        2850            JAI               3098          HYD   
8           6E        2850            GOI               3007          HYD   
9           6E        2850            BBI               3042          HYD   

   dest_airport_id codeshare  stops equipment  _data_source  \
0             <NA>      None      0       CR2  our-airports   
1             <NA>      None      0       AN4  our-airports   
2             <NA>      None      0       SU9  our-airports   
3             <NA>      None      0       BEH  our-airports   
4             <NA>      None      0       320  our-airports   
5             <NA>      None      0       320  our-airports   
6             <NA>      None      0       320  our-airports   
7             <NA>      None      0       320  our-airports   
8             <NA>      None      0       320  our-airports   
9             <NA>      None      0       320  our-airports   

                        _load_time  
0 2025-09-06 02:42:52.369196+00:00  
1 2025-09-06 02:42:52.369196+00:00  
2 2025-09-06 02:42:52.369196+00:00  
3 2025-09-06 02:42:52.369196+00:00  
4 2025-09-06 02:42:52.369196+00:00  
5 2025-09-06 02:42:52.369196+00:00  
6 2025-09-06 02:42:52.369196+00:00  
7 2025-09-06 02:42:52.369196+00:00  
8 2025-09-06 02:42:52.369196+00:00  
9 2025-09-06 02:42:52.369196+00:00

##### Map the source and destination iata codes to their icao codes

In [ ]:
%%bigquery
select r.airline_id, a1.icao as source_airport_icao, a2.icao as dest_airport_icao, r.codeshare, r.stops, r.equipment, r._data_source, r._load_time
from air_travel_stg.flight_routes r
join air_travel_int.Airport a1
on r.source_airport = a1.iata
join air_travel_int.Airport a2
on r.dest_airport = a2.iata

Query is running:   0%|          |

Downloading:   0%|          |

airline_id source_airport_icao dest_airport_icao codeshare  stops  \
0             410                UUDD              URRZ      None      0   
1           17885                MMMX              MMMK      None      0   
2           18946                FACT              KPBZ      None      0   
3            4550               SLT L              SLOR      None      0   
4            1392                HUGE              HUKO      None      0   
...           ...                 ...               ...       ...    ...   
46800       16508                FZNA              FZNJ      None      0   
46801       16508                FZAA              FZFU      None      0   
46802       16508                FZHC              FZVC      None      0   
46803         690                ZWWW              ZWBK      None      0   
46804         324                RJTT              PWMI      None      0   

      equipment  _data_source                       _load_time  
0           CR2  our-airports 2025-09-06 02:42:52.369196+00:00  
1           SU9  our-airports 2025-09-06 02:42:52.369196+00:00  
2           BEH  our-airports 2025-09-06 02:42:52.369196+00:00  
3           SWM  our-airports 2025-09-06 02:42:52.369196+00:00  
4           CNA  our-airports 2025-09-06 02:42:52.369196+00:00  
...         ...           ...                              ...  
46800       F50  our-airports 2025-09-06 02:42:52.369196+00:00  
46801       L4T  our-airports 2025-09-06 02:42:52.369196+00:00  
46802       F50  our-airports 2025-09-06 02:42:52.369196+00:00  
46803       E90  our-airports 2025-09-06 02:42:52.369196+00:00  
46804   737 738  our-airports 2025-09-06 02:42:52.369196+00:00  

[46805 rows x 8 columns]

##### Create the final table

In [ ]:
%%bigquery
create or replace table air_travel_int.Flight_Routes as
  select distinct r.airline_id, a1.icao as source_airport_icao, a2.icao as dest_airport_icao, r.codeshare, r.stops, r.equipment, r._data_source, r._load_time
  from air_travel_stg.flight_routes r
  join air_travel_int.Airport a1
  on r.source_airport = a1.iata
  join air_travel_int.Airport a2
  on r.dest_airport = a2.iata

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
select * from air_travel_int.Flight_Routes

Query is running:   0%|          |

Downloading:   0%|          |

airline_id source_airport_icao dest_airport_icao codeshare  stops  \
0              24                KMSY              KAUS      None      0   
1              24                KAUS              KMSY      None      0   
2              28                KATL              KJFK      None      0   
3             109                PAIL              PANC      None      0   
4             109                PANC              PAIL      None      0   
...           ...                 ...               ...       ...    ...   
43913        4026                ZYHB              ZBGX      None      0   
43914        4026                ZBHZ              ZYHB      None      0   
43915        4026                ZYHB              ZBHZ      None      0   
43916        4026                ZGXK              ZYHB      None      0   
43917        4026                ZBGX              ZYHB      None      0   

      equipment  _data_source                       _load_time  
0          None  our-airports 2025-09-06 02:42:52.369196+00:00  
1          None  our-airports 2025-09-06 02:42:52.369196+00:00  
2          None  our-airports 2025-09-06 02:42:52.369196+00:00  
3          None  our-airports 2025-09-06 02:42:52.369196+00:00  
4          None  our-airports 2025-09-06 02:42:52.369196+00:00  
...         ...           ...                              ...  
43913       YN7  our-airports 2025-09-06 02:42:52.369196+00:00  
43914       YN7  our-airports 2025-09-06 02:42:52.369196+00:00  
43915       YN7  our-airports 2025-09-06 02:42:52.369196+00:00  
43916       YN7  our-airports 2025-09-06 02:42:52.369196+00:00  
43917       YN7  our-airports 2025-09-06 02:42:52.369196+00:00  

[43918 rows x 8 columns]

##### Check the primary key fields for uniqueness (airline_id, source_airport_icao, dest_airport_icao)

In [ ]:
%%bigquery
select airline_id, source_airport_icao, dest_airport_icao, count(*)
from air_travel_int.Flight_Routes
group by airline_id, source_airport_icao, dest_airport_icao
having count(*) > 1

Query is running:   0%|          |

Downloading:   0%|          |

airline_id source_airport_icao dest_airport_icao  f0_
0        <NA>                CYZV             CYW B    3
1        <NA>               CYW B              CYFV    2
2        <NA>               CYW B              CYZV    3
3        <NA>                CYFV             CYW B    2
4        <NA>                CYQB              CYZV    2
5        <NA>                CYZV              CYQB    2
6        <NA>                CYQB              CYUL    2
7        <NA>                CYUL              CYQB    2

##### Cannot have a component of the primary key be null, so delete all the null airline_id's

In [ ]:
%%bigquery
delete from air_travel_int.Flight_Routes
where airline_id is null

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
select airline_id, source_airport_icao, dest_airport_icao, count(*)
from air_travel_int.Flight_Routes
group by airline_id, source_airport_icao, dest_airport_icao
having count(*) > 1

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [airline_id, source_airport_icao, dest_airport_icao, f0_]
Index: []

In [ ]:
%%bigquery
select * from air_travel_int.Flight_Routes
where equipment is not null

Query is running:   0%|          |

Downloading:   0%|          |

airline_id source_airport_icao dest_airport_icao codeshare  stops  \
0            4547                KATL              KFLL      None      0   
1            3090                EHAM              KATL      None      0   
2             328                AYMH              AYWK      None      0   
3             328                AYPY              AYMH      None      0   
4             328                AYPY              AYBK      None      0   
...           ...                 ...               ...       ...    ...   
43650        4026                ZYHB              ZBHZ      None      0   
43651        4026                ZBGX              ZYHB      None      0   
43652        4026                ZYHB              ZGXK      None      0   
43653        4026                ZGXK              ZYHB      None      0   
43654        4026                ZYHB              ZBGX      None      0   

          equipment  _data_source                       _load_time  
0       73W 733 73C  our-airports 2025-09-06 02:42:52.369196+00:00  
1               777  our-airports 2025-09-06 02:42:52.369196+00:00  
2               100  our-airports 2025-09-06 02:42:52.369196+00:00  
3               100  our-airports 2025-09-06 02:42:52.369196+00:00  
4               100  our-airports 2025-09-06 02:42:52.369196+00:00  
...             ...           ...                              ...  
43650           YN7  our-airports 2025-09-06 02:42:52.369196+00:00  
43651           YN7  our-airports 2025-09-06 02:42:52.369196+00:00  
43652           YN7  our-airports 2025-09-06 02:42:52.369196+00:00  
43653           YN7  our-airports 2025-09-06 02:42:52.369196+00:00  
43654           YN7  our-airports 2025-09-06 02:42:52.369196+00:00  

[43655 rows x 8 columns]

##### Equipment is a list of elements and appears to connect to `Aircraft.iata`. Need to validate. Either way, equipment can't stay as a list because it needs to join to the Aicraft table

In [ ]:
%%bigquery
select * from air_travel_int.Aircraft where iata = '733'

Query is running:   0%|          |

Downloading:   0%|          |

icao iata            name _data_source                       _load_time
0  B733  733  Boeing 737-300  openflights 2025-09-06 02:42:39.189193+00:00

##### Flatten the equipment field from Flight_Routes and store it in its own table. This will resolve anomaly type 8. We'll call the new table Route_Equipment

In [ ]:
%%bigquery
select airline_id, source_airport_icao, dest_airport_icao, split(trim(equipment), ' ') as equipment_array,
  _data_source, _load_time
from air_travel_int.Flight_Routes
where equipment is not null

Query is running:   0%|          |

Downloading:   0%|          |

airline_id source_airport_icao dest_airport_icao  equipment_array  \
0            4547                KATL              KFLL  [73W, 733, 73C]   
1            3090                EHAM              KATL            [777]   
2             328                AYMH              AYWK            [100]   
3             328                AYPY              AYMH            [100]   
4             328                AYPY              AYBK            [100]   
...           ...                 ...               ...              ...   
43650        4026                ZYHB              ZBHZ            [YN7]   
43651        4026                ZBGX              ZYHB            [YN7]   
43652        4026                ZYHB              ZGXK            [YN7]   
43653        4026                ZGXK              ZYHB            [YN7]   
43654        4026                ZYHB              ZBGX            [YN7]   

       _data_source                       _load_time  
0      our-airports 2025-09-06 02:42:52.369196+00:00  
1      our-airports 2025-09-06 02:42:52.369196+00:00  
2      our-airports 2025-09-06 02:42:52.369196+00:00  
3      our-airports 2025-09-06 02:42:52.369196+00:00  
4      our-airports 2025-09-06 02:42:52.369196+00:00  
...             ...                              ...  
43650  our-airports 2025-09-06 02:42:52.369196+00:00  
43651  our-airports 2025-09-06 02:42:52.369196+00:00  
43652  our-airports 2025-09-06 02:42:52.369196+00:00  
43653  our-airports 2025-09-06 02:42:52.369196+00:00  
43654  our-airports 2025-09-06 02:42:52.369196+00:00  

[43655 rows x 6 columns]

In [ ]:
%%bigquery
create or replace table air_travel_int.Route_Equipment as
  select airline_id, source_airport_icao, dest_airport_icao, equipment, _data_source, _load_time
  from (
    select airline_id, source_airport_icao, dest_airport_icao, split(trim(equipment), ' ') as equipment_array,
      _data_source, _load_time
    from air_travel_int.Flight_Routes
    where equipment is not null) r, unnest(r.equipment_array) as equipment

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
select * from air_travel_int.Route_Equipment
limit 10

Query is running:   0%|          |

Downloading:   0%|          |

airline_id source_airport_icao dest_airport_icao equipment  _data_source  \
0         328                AYKV              AYMO       100  our-airports   
1        2923                OISS              OIAS       100  our-airports   
2        4304                LPPT              LPPR       ER4  our-airports   
3         491                LOWW              UMMS       F70  our-airports   
4         491                LIPB              LOWW       DH4  our-airports   
5        1317                MDPC              CYUL       310  our-airports   
6        1317                CYUL              MMUN       310  our-airports   
7        3871                OMSJ              OPPS       320  our-airports   
8         596                EDDL              LFPG       320  our-airports   
9        3764                SBGR              SBFL       320  our-airports   

                        _load_time  
0 2025-09-06 02:42:52.369196+00:00  
1 2025-09-06 02:42:52.369196+00:00  
2 2025-09-06 02:42:52.369196+00:00  
3 2025-09-06 02:42:52.369196+00:00  
4 2025-09-06 02:42:52.369196+00:00  
5 2025-09-06 02:42:52.369196+00:00  
6 2025-09-06 02:42:52.369196+00:00  
7 2025-09-06 02:42:52.369196+00:00  
8 2025-09-06 02:42:52.369196+00:00  
9 2025-09-06 02:42:52.369196+00:00

##### Connect the equipment to the Aircraft table

In [ ]:
%%bigquery
select count(*)
from air_travel_int.Route_Equipment
where equipment not in (select iata from air_travel_int.Aircraft)

Query is running:   0%|          |

Downloading:   0%|          |

f0_
0    0

##### The tables connect, but we want to change to mapping to icao instead of iata. That's because the Aircraft table uses the icao code as its primary key and we cannot rely on the iata being unique

In [ ]:
%%bigquery
select distinct re.airline_id, re.source_airport_icao, re.dest_airport_icao,
  a.icao as icao_equipment, re._data_source, re._load_time
from air_travel_int.Route_Equipment re join air_travel_int.Aircraft a
on re.equipment = a.iata

Query is running:   0%|          |

Downloading:   0%|          |

airline_id source_airport_icao dest_airport_icao icao_equipment  \
0             328                AYKV              AYMO           F100   
1            2923                OISS              OIAS           F100   
2            4304                LPPT              LPPR           E145   
3            1317                MDPC              CYUL           A310   
4            1317                CYUL              MMUN           A310   
...           ...                 ...               ...            ...   
52157        5461                ESGP              LHBP           A320   
52158        5461                LBSF              LIRF           A320   
52159        5461                LRCL              LLBG           A320   
52160        5461                EVRA              EHEH           A320   
52161        5461                EPWA              EGPF           A320   

       _data_source                       _load_time  
0      our-airports 2025-09-06 02:42:52.369196+00:00  
1      our-airports 2025-09-06 02:42:52.369196+00:00  
2      our-airports 2025-09-06 02:42:52.369196+00:00  
3      our-airports 2025-09-06 02:42:52.369196+00:00  
4      our-airports 2025-09-06 02:42:52.369196+00:00  
...             ...                              ...  
52157  our-airports 2025-09-06 02:42:52.369196+00:00  
52158  our-airports 2025-09-06 02:42:52.369196+00:00  
52159  our-airports 2025-09-06 02:42:52.369196+00:00  
52160  our-airports 2025-09-06 02:42:52.369196+00:00  
52161  our-airports 2025-09-06 02:42:52.369196+00:00  

[52162 rows x 6 columns]

##### Replace the Route_Equipment table

In [ ]:
%%bigquery
create or replace table air_travel_int.Route_Equipment as
  select distinct re.airline_id, re.source_airport_icao, re.dest_airport_icao,
    a.icao as icao_equipment, re._data_source, re._load_time
  from air_travel_int.Route_Equipment re join air_travel_int.Aircraft a
  on re.equipment = a.iata

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Check the uniqueness of the primary key

In [ ]:
%%bigquery
select airline_id, source_airport_icao, dest_airport_icao, icao_equipment, count(*)
from air_travel_int.Route_Equipment
group by airline_id, source_airport_icao, dest_airport_icao, icao_equipment
having count(*) > 1

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [airline_id, source_airport_icao, dest_airport_icao, icao_equipment, f0_]
Index: []

##### No need to recheck the foreign key columns since we already checked them for the Flight_Routes table which sourced this table

#### Create the Flight_Delays table (resolving anomaly types 9 and 10)

##### Note: The flight delay data was produced by the U.S. Department of Transportation's Bureau of Transportation Statistics (BTS) and it only tracks US flights

In [ ]:
%%bigquery
select * from air_travel_stg.flight_delays
limit 10

Query is running:   0%|          |

Downloading:   0%|          |

event_month carrier            carrier_name airport_code airport_city  \
0  2003-09-01      TZ  ATA Airlines d/b/a ATA          ABQ  Albuquerque   
1  2006-01-01      TZ  ATA Airlines d/b/a ATA          BWI    Baltimore   
2  2004-03-01      TZ  ATA Airlines d/b/a ATA          BWI    Baltimore   
3  2004-11-01      TZ  ATA Airlines d/b/a ATA          CLT    Charlotte   
4  2004-10-01      TZ  ATA Airlines d/b/a ATA          CLT    Charlotte   
5  2005-01-01      TZ  ATA Airlines d/b/a ATA          CLT    Charlotte   
6  2003-12-01      TZ  ATA Airlines d/b/a ATA          CLT    Charlotte   
7  2003-11-01      TZ  ATA Airlines d/b/a ATA          CLT    Charlotte   
8  2004-03-01      TZ  ATA Airlines d/b/a ATA          CLT    Charlotte   
9  2004-07-01      TZ  ATA Airlines d/b/a ATA          CLT    Charlotte   

  airport_state                                       airport_name  arr_total  \
0            NM                  Albuquerque International Sunport       <NA>   
1            MD   Baltimore/Washington International Thurgood M...       <NA>   
2            MD   Baltimore/Washington International Thurgood M...       <NA>   
3            NC                    Charlotte Douglas International        107   
4            NC                    Charlotte Douglas International        114   
5            NC                    Charlotte Douglas International          8   
6            NC                    Charlotte Douglas International        105   
7            NC                    Charlotte Douglas International        103   
8            NC                    Charlotte Douglas International        112   
9            NC                    Charlotte Douglas International        106   

   arr_cancelled  arr_diverted  arr_delay_min  weather_delay_min  \
0           <NA>          <NA>           <NA>               <NA>   
1           <NA>          <NA>           <NA>               <NA>   
2           <NA>          <NA>           <NA>               <NA>   
3              0             0            603                  0   
4              2             0            374                  0   
5              0             0             86                  0   
6              0             0            883                  0   
7              1             0            826                  0   
8              0             0            479                  0   
9              0             0           1687                  0   

   nas_delay_min  late_aircraft_delay_min         _data_source  \
0           <NA>                     <NA>  on-time-performance   
1           <NA>                     <NA>  on-time-performance   
2           <NA>                     <NA>  on-time-performance   
3            164                      269  on-time-performance   
4            224                       97  on-time-performance   
5             24                        5  on-time-performance   
6            279                      423  on-time-performance   
7            194                      507  on-time-performance   
8             78                      287  on-time-performance   
9            504                      932  on-time-performance   

                        _load_time  
0 2025-09-05 17:00:47.734796+00:00  
1 2025-09-05 17:00:47.734796+00:00  
2 2025-09-05 17:00:47.734796+00:00  
3 2025-09-05 17:00:47.734796+00:00  
4 2025-09-05 17:00:47.734796+00:00  
5 2025-09-05 17:00:47.734796+00:00  
6 2025-09-05 17:00:47.734796+00:00  
7 2025-09-05 17:00:47.734796+00:00  
8 2025-09-05 17:00:47.734796+00:00  
9 2025-09-05 17:00:47.734796+00:00

In [1]:
%%bigquery
select distinct fd.event_month, fd.carrier, fd.carrier_name, a.icao as airport_icao,
    fd.arr_total, fd.arr_cancelled, fd.arr_diverted, fd.arr_delay_min,
    fd.carrier_delay_min, fd.weather_delay_min, fd.nas_delay_min,
    fd.late_aircraft_delay_min, fd._data_source, fd._load_time
from air_travel_stg.flight_delays fd join air_travel_int.Airport a
on fd.airport_code = a.iata
where a.country_code = 'US'
and fd.arr_total is not null

Query is running:   0%|          |

Downloading:   0%|          |

event_month carrier            carrier_name airport_icao  arr_total  \
0       2004-04-01      TZ  ATA Airlines d/b/a ATA          CLT        107   
1       2003-07-01      TZ  ATA Airlines d/b/a ATA          CLT        111   
2       2004-01-01      TZ  ATA Airlines d/b/a ATA          CLT        107   
3       2003-10-01      TZ  ATA Airlines d/b/a ATA          CLT        113   
4       2003-12-01      TZ  ATA Airlines d/b/a ATA          CLT        105   
...            ...     ...                     ...          ...        ...   
363695  2016-02-01      VX          Virgin America         KIAD        102   
363696  2017-05-01      VX          Virgin America         KIAD        142   
363697  2018-01-01      VX          Virgin America         KIAD        116   
363698  2012-12-01      VX          Virgin America         KIAD        167   
363699  2013-12-01      VX          Virgin America         KIAD        137   

        arr_cancelled  arr_diverted  arr_delay_min  carrier_delay_min  \
0                   0             0            357                 76   
1                   0             0           2229                160   
2                   5             0           1798                310   
3                   0             0            101                 21   
4                   0             0            883                181   
...               ...           ...            ...                ...   
363695              3             1            404                202   
363696              0             0           1930                508   
363697              0             0            559                420   
363698              0             0           1224                191   
363699              1             0            502                327   

        weather_delay_min  nas_delay_min  late_aircraft_delay_min  \
0                       0            151                      130   
1                       0            933                     1136   
2                     176            334                      978   
3                       0             16                       64   
4                       0            279                      423   
...                   ...            ...                      ...   
363695                 26             36                      140   
363696                 26            380                      990   
363697                  0            139                        0   
363698                 17             89                      927   
363699                 64             25                       86   

               _data_source                       _load_time  
0       on-time-performance 2025-09-05 17:00:47.734796+00:00  
1       on-time-performance 2025-09-05 17:00:47.734796+00:00  
2       on-time-performance 2025-09-05 17:00:47.734796+00:00  
3       on-time-performance 2025-09-05 17:00:47.734796+00:00  
4       on-time-performance 2025-09-05 17:00:47.734796+00:00  
...                     ...                              ...  
363695  on-time-performance 2025-09-05 17:00:47.734796+00:00  
363696  on-time-performance 2025-09-05 17:00:47.734796+00:00  
363697  on-time-performance 2025-09-05 17:00:47.734796+00:00  
363698  on-time-performance 2025-09-05 17:00:47.734796+00:00  
363699  on-time-performance 2025-09-05 17:00:47.734796+00:00  

[363700 rows x 14 columns]

##### Map the carrier name to the Airline table and replace the carrier and carrier name with the airline id

In [2]:
%%bigquery
select distinct fd.event_month, fd.carrier, fd.carrier_name, al.id as airline_id, ap.icao as airport_icao,
    fd.arr_total, fd.arr_cancelled, fd.arr_diverted, fd.arr_delay_min,
    fd.carrier_delay_min, fd.weather_delay_min, fd.nas_delay_min, fd.late_aircraft_delay_min,
    fd._data_source, fd._load_time
from air_travel_stg.flight_delays fd join air_travel_int.Airport ap
on fd.airport_code = ap.iata
join air_travel_int.Airline al
on fd.carrier_name = al.name
where ap.country_code = 'US'
and fd.arr_total is not null

Query is running:   0%|          |

Downloading:   0%|          |

event_month carrier    carrier_name  airline_id airport_icao  arr_total  \
0      2023-11-01      G4   Allegiant Air          35         KSPI         10   
1      2022-12-01      G4   Allegiant Air          35         KSPI         20   
2      2018-05-01      G4   Allegiant Air          35         KSPI          9   
3      2022-01-01      G4   Allegiant Air          35         KSPI         18   
4      2019-05-01      G4   Allegiant Air          35         KSPI          9   
...           ...     ...             ...         ...          ...        ...   
82573  2016-02-01      VX  Virgin America        5331         KIAD        102   
82574  2017-05-01      VX  Virgin America        5331         KIAD        142   
82575  2018-01-01      VX  Virgin America        5331         KIAD        116   
82576  2012-12-01      VX  Virgin America        5331         KIAD        167   
82577  2013-12-01      VX  Virgin America        5331         KIAD        137   

       arr_cancelled  arr_diverted  arr_delay_min  carrier_delay_min  \
0                  0             0             48                  0   
1                  0             0            102                 20   
2                  0             0            143                  0   
3                  2             0            370                 80   
4                  0             0              0                  0   
...              ...           ...            ...                ...   
82573              3             1            404                202   
82574              0             0           1930                508   
82575              0             0            559                420   
82576              0             0           1224                191   
82577              1             0            502                327   

       weather_delay_min  nas_delay_min  late_aircraft_delay_min  \
0                     34             14                        0   
1                     82              0                        0   
2                      0              0                      143   
3                     15             49                      226   
4                      0              0                        0   
...                  ...            ...                      ...   
82573                 26             36                      140   
82574                 26            380                      990   
82575                  0            139                        0   
82576                 17             89                      927   
82577                 64             25                       86   

              _data_source                       _load_time  
0      on-time-performance 2025-09-05 17:00:47.734796+00:00  
1      on-time-performance 2025-09-05 17:00:47.734796+00:00  
2      on-time-performance 2025-09-05 17:00:47.734796+00:00  
3      on-time-performance 2025-09-05 17:00:47.734796+00:00  
4      on-time-performance 2025-09-05 17:00:47.734796+00:00  
...                    ...                              ...  
82573  on-time-performance 2025-09-05 17:00:47.734796+00:00  
82574  on-time-performance 2025-09-05 17:00:47.734796+00:00  
82575  on-time-performance 2025-09-05 17:00:47.734796+00:00  
82576  on-time-performance 2025-09-05 17:00:47.734796+00:00  
82577  on-time-performance 2025-09-05 17:00:47.734796+00:00  

[82578 rows x 15 columns]

##### Create the final table

In [3]:
%%bigquery
create or replace table air_travel_int.Flight_Delays as
  select distinct fd.event_month, al.id as airline_id, ap.icao as airport_icao,
    fd.arr_total, fd.arr_cancelled, fd.arr_diverted, fd.arr_delay_min,
    fd.carrier_delay_min, fd.weather_delay_min, fd.nas_delay_min,
    fd.late_aircraft_delay_min, fd._data_source, fd._load_time
  from air_travel_stg.flight_delays fd join air_travel_int.Airport ap
  on fd.airport_code = ap.iata
  join air_travel_int.Airline al
  on fd.carrier_name = al.name
  where ap.country_code = 'US'
  and fd.arr_total is not null

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [4]:
%%bigquery
select * from air_travel_int.Flight_Delays
order by event_month desc
limit 10

Query is running:   0%|          |

Downloading:   0%|          |

event_month  airline_id airport_icao  arr_total  arr_cancelled  \
0  2024-04-01          35         KMSY          9              0   
1  2024-04-01        2778         KOAK         72              0   
2  2024-04-01       19619         KRST         38              0   
3  2024-04-01          35         KSCK         36              0   
4  2024-04-01          35         KMMT         31              0   
5  2024-04-01        4687         KLBE         51              0   
6  2024-04-01        2778         KSBA         23              0   
7  2024-04-01        3029         KSEA         60              0   
8  2024-04-01        2468         KSMF         26              0   
9  2024-04-01          35         KSDF         53              0   

   arr_diverted  arr_delay_min  carrier_delay_min  weather_delay_min  \
0             0             37                 37                  0   
1             0            195                149                  0   
2             0            444                 80                140   
3             0            284                166                 14   
4             0             43                  0                  0   
5             0            184                 62                  0   
6             0             56                 10                  0   
7             0           1923                982                 82   
8             0            714                 94                  0   
9             0            390                 94                  0   

   nas_delay_min  late_aircraft_delay_min         _data_source  \
0              0                        0  on-time-performance   
1             46                        0  on-time-performance   
2            155                       69  on-time-performance   
3             32                       72  on-time-performance   
4             43                        0  on-time-performance   
5            116                        6  on-time-performance   
6             46                        0  on-time-performance   
7            391                      468  on-time-performance   
8              7                      613  on-time-performance   
9            158                      115  on-time-performance   

                        _load_time  
0 2025-09-05 17:00:47.734796+00:00  
1 2025-09-05 17:00:47.734796+00:00  
2 2025-09-05 17:00:47.734796+00:00  
3 2025-09-05 17:00:47.734796+00:00  
4 2025-09-05 17:00:47.734796+00:00  
5 2025-09-05 17:00:47.734796+00:00  
6 2025-09-05 17:00:47.734796+00:00  
7 2025-09-05 17:00:47.734796+00:00  
8 2025-09-05 17:00:47.734796+00:00  
9 2025-09-05 17:00:47.734796+00:00

##### Check uniqueness of primary key fields (`event_month`, `airline_id`, `airport_icao`)

In [ ]:
%%bigquery
select event_month, airline_id, airport_icao, count(*) as count
from air_travel_int.Flight_Delays
group by event_month, airline_id, airport_icao
having count(*) > 1

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [event_month, airline_id, airport_icao, count]
Index: []

##### Recheck foreign key constraints

In [ ]:
%%bigquery
select count(*)
from air_travel_int.Flight_Delays
where airline_id not in (select id from air_travel_int.Airline)

Query is running:   0%|          |

Downloading:   0%|          |

f0_
0    0

In [ ]:
%%bigquery
select count(*)
from air_travel_int.Flight_Delays
where airport_icao not in (select icao from air_travel_int.Airport)

Query is running:   0%|          |

Downloading:   0%|          |

f0_
0    0

#### Key Constraints
##### More details on how primary and foreign keys work in BQ: [link](https://cloud.google.com/blog/products/data-analytics/join-optimizations-with-bigquery-primary-and-foreign-keys?e=48754805)

##### Primary keys

In [ ]:
%%bigquery
alter table air_travel_int.Aircraft add primary key (icao) not enforced;
alter table air_travel_int.Airline add primary key (id) not enforced;
alter table air_travel_int.Airport add primary key (icao) not enforced;
alter table air_travel_int.Airport_Concessions add primary key (airport_icao, terminal, business, location) not enforced;
alter table air_travel_int.Airport_Establishment add primary key (business) not enforced;
alter table air_travel_int.Airport_Review add primary key (id) not enforced;
alter table air_travel_int.Country add primary key (iso_code) not enforced;
alter table air_travel_int.Flight_Delays add primary key (event_month, airline_id, airport_icao) not enforced;
alter table air_travel_int.Flight_Routes add primary key (airline_id, source_airport_icao, dest_airport_icao) not enforced;
alter table air_travel_int.Food_Beverage add primary key (business, menu_item) not enforced;
alter table air_travel_int.Route_Equipment add primary key (airline_id, source_airport_icao, dest_airport_icao) not enforced;
alter table air_travel_int.TSA_Traffic add primary key (event_date, event_hour, airport_icao, security_checkpoint) not enforced;

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Foreign keys

In [ ]:
%%bigquery
alter table air_travel_int.Airline add constraint airline_fk_country foreign key (country_code)
    references air_travel_int.Country (iso_code) not enforced;
alter table air_travel_int.Airport add constraint airport_fk_country foreign key (country_code)
    references air_travel_int.Country (iso_code) not enforced;
alter table air_travel_int.Airport_Concessions add constraint airport_concess_fk_icao foreign key (airport_icao)
    references air_travel_int.Airport (icao) not enforced;
alter table air_travel_int.Airport_Review add constraint airport_reviews_fk_icao foreign key (airport_icao)
    references air_travel_int.Airport (icao) not enforced;
alter table air_travel_int.Flight_Delays add constraint flight_delays_fk_airline_id foreign key (airline_id)
    references air_travel_int.Airline (id) not enforced;
alter table air_travel_int.Flight_Delays add constraint flight_delays_fk_airport_icao foreign key (airport_icao)
    references air_travel_int.Airport (icao) not enforced;
alter table air_travel_int.Flight_Routes add constraint flight_routes_fk_airline_id foreign key (airline_id)
    references air_travel_int.Airline (id) not enforced;
alter table air_travel_int.Flight_Routes add constraint flight_routes_fk_source_airport_icao foreign key (source_airport_icao)
    references air_travel_int.Airport (icao) not enforced;
alter table air_travel_int.Flight_Routes add constraint flight_routes_fk_dest_airport_icao foreign key (dest_airport_icao)
    references air_travel_int.Airport (icao) not enforced;
alter table air_travel_int.Food_Beverage add constraint food_beverage_fk_business foreign key (business)
    references air_travel_int.Airport_Establishment (business) not enforced;
alter table air_travel_int.Route_Equipment add constraint route_equipment_fk_airline_id foreign key (airline_id)
    references air_travel_int.Airline (id) not enforced;
alter table air_travel_int.Route_Equipment add constraint route_equipment_fk_source_airport_icao foreign key (source_airport_icao)
    references air_travel_int.Airport (icao) not enforced;
alter table air_travel_int.Route_Equipment add constraint route_equipment_fk_dest_airport_icao foreign key (dest_airport_icao)
    references air_travel_int.Airport (icao) not enforced;
alter table air_travel_int.Route_Equipment add constraint route_equipment_fk_equipment foreign key (icao_equipment)
    references air_travel_int.Aircraft (icao) not enforced;
alter table air_travel_int.TSA_Traffic add constraint tsa_traffic_fk_airport_icao foreign key (airport_icao)
    references air_travel_int.Airport (icao) not enforced;

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

#### (Optional) Restart the runtime
##### Run this cell only if you see that your Colab's performance is degrading and your code changes aren't getting picked up. Be sure to save your notebook before running this cell.

In [ ]:
import os
os.kill(os.getpid(), 9)